### Create the intermediate layer for the Air Travel warehouse



#### Declare variables used throughout

In [60]:
project_id = "cs329e-sp2025"
region = "us-central1"
model_name = "gemini-2.0-flash-001"
dataset = "air_travel_int"
region = "us-central1"

#### Create BQ dataset for storing the intermediate data

In [5]:
from google.cloud import bigquery

bq_client = bigquery.Client()

dataset_id = bigquery.Dataset(f"{project_id}.{dataset}")
dataset_id.location = region
resp = bq_client.create_dataset(dataset_id, exists_ok=True)
print("Created dataset {}.{}".format(bq_client.project, resp.dataset_id))

Created dataset cs329e-sp2025.air_travel_int


#### `Airport` table (criteria 9)

##### Goal: come up with a universal airport identifier. Intuitively, we would like to use the IATA code because it is the one that most people are familiar with. The problem is that this code is not globally unique, and we would need to pair it up with the country where the airport is located.

##### Instead of `{iata, country}`, we will use the ICAO code, which is globally unique. Unfortunately, there are many records in the airports table which are missing an icao code. We will attempt to use the LLM to look them up, but we need to watch out for hallucinations.

##### We want to end up with distinct airports in the table and only airports. We will remove all other records from the table, including duplicate airports and non-airports.

##### Once the aiport table is ready, we will re-create the child tables so that they reference the new airport identifier.


##### Before creating the new Airport table, we want to see if we can enrich it with the airport state. This data is not in the airports staging table, but it's  available from the `tsa_traffic` table (for US airports only).

In [9]:
%%bigquery
select distinct a.airport_id, a.icao, a.iata, a.airport_name, a.city, a.country, t.airport_state
from air_travel_stg.airports a
left join air_travel_stg.tsa_traffic t
on a.iata = t.airport_code
where a.country = 'United States'
and t.airport_state is not null

Query is running:   0%|          |

Downloading:   0%|          |

airport_id  icao iata                                       airport_name  \
0          5959  PADK  ADK                                       Adak Airport   
1          3460  PADL  DLG                                 Dillingham Airport   
2          3808  PAKT  KTN                    Ketchikan International Airport   
3          3492  PAJN  JNU                       Juneau International Airport   
4          3620  PASC  SCC                                  Deadhorse Airport   
..          ...   ...  ...                                                ...   
362        3728  PHNL  HNL              Daniel K Inouye International Airport   
363        3415  PHTO  ITO                         Hilo International Airport   
364        3602  PHLI  LIH                                      Lihue Airport   
365        3514  PHKO  KOA  Ellison Onizuka Kona International At Keahole ...   
366        3456  PHOG  OGG                                    Kahului Airport   

            city        country airport_state  
0    Adak Island  United States            AK  
1     Dillingham  United States            AK  
2      Ketchikan  United States            AK  
3         Juneau  United States            AK  
4      Deadhorse  United States            AK  
..           ...            ...           ...  
362     Honolulu  United States            HI  
363         Hilo  United States            HI  
364        Lihue  United States            HI  
365         Kona  United States            HI  
366      Kahului  United States            HI  

[367 rows x 7 columns]

##### Note: icao code KSGU should not be appearing twice. This is a problem.

In [10]:
%%bigquery
select * from air_travel_stg.tsa_traffic
where airport_code = 'SGU'

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_code          airport_name airport_city  \
0  2023-06-21           6          SGU  St. George Municipal   St. George   
1  2023-02-15          12          SGU   Shreveport Regional   Shreveport   
2  2024-07-24          12          SGU    St George Regional   St. George   
3  2023-11-08          12          SGU    St George Regional   St. George   
4  2024-03-13          12          SGU    St George Regional   St. George   
5  2024-03-20          12          SGU    St George Regional   St. George   
6  2022-08-17          12          SGU  St. George Municipal   St. George   

  airport_state    tsa_checkpoint  passenger_count _data_source  \
0            UT              SGUZ               30     tsa-foia   
1            LA  Checkpoint SHV01               71     tsa-foia   
2            UT              SGUZ               58     tsa-foia   
3            UT              SGUZ               82     tsa-foia   
4            UT              SGUZ               44     tsa-foia   
5            UT              SGUZ               33     tsa-foia   
6            UT              SGUZ               62     tsa-foia   

                        _load_time  
0 2025-01-24 19:01:52.052444+00:00  
1 2025-01-24 18:59:34.710863+00:00  
2 2025-01-24 19:00:51.382580+00:00  
3 2025-01-24 19:03:38.477990+00:00  
4 2025-01-24 19:02:18.411282+00:00  
5 2025-01-24 19:02:33.313392+00:00  
6 2025-01-24 18:58:23.959199+00:00

###### Note: Shreveport Regional was assigned the wrong iata code, should be SHV instead of SGU

In [11]:
%%bigquery
select icao, count(*) as duplicate_icao_records
from
(select distinct a.airport_id, a.icao, a.iata, a.airport_name, a.city, a.country, t.airport_state
from air_travel_stg.airports a
left join air_travel_stg.tsa_traffic t
on a.iata = t.airport_code
where a.country = 'United States'
and t.airport_state is not null)
group by icao
having count(*) > 1

Query is running:   0%|          |

Downloading:   0%|          |

icao  duplicate_icao_records
0   PANC                       2
1   KBRD                       2
2   KAMA                       2
3   KSHV                       2
4   KGRB                       2
5   KCPR                       2
6   KCNY                       2
7   KSGU                       2
8   KFAT                       2
9   KCRW                       2
10  KLWB                       2
11  KPKB                       2
12  KATL                       2
13  KHTS                       2
14  KLBE                       2
15  KSHD                       2

##### Want to leave out the above icao codes because they are associated with more than one state in the tsa_traffic table and one of the two values is wrong and we don't know which one.

In [12]:
%%bigquery
create or replace table air_travel_int.tmp_duplicate_icao as
  select icao
  from
    (select distinct a.airport_id, a.icao, a.iata, a.airport_name, a.city, a.country, t.airport_state
    from air_travel_stg.airports a
    left join air_travel_stg.tsa_traffic t
    on a.iata = t.airport_code
    where a.country = 'United States'
    and t.airport_state is not null)
  group by icao
  having count(*) > 1

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Create the Airport table in three statements, first add US airports with state values, then add the remaining US airports without states and lastly add non-US airports.

In [13]:
%%bigquery
create or replace table air_travel_int.Airport as
  select distinct a.icao, a.iata, a.airport_name as name,
      a.city, tsa.airport_state as state, a.country,
      a.latitude, a.longitude, a.altitude, a.timezone_name, a.timezone_delta, a.daylight_savings_time,
      a.type, a.source, a._data_source, a._load_time
  from air_travel_stg.airports a
  left join air_travel_stg.tsa_traffic tsa
  on a.iata = tsa.airport_code
  where a.country = 'United States'
  and a.type in ('airport', NULL)
  and a.icao not in (select icao from air_travel_int.tmp_duplicate_icao)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [14]:
%%bigquery
insert into air_travel_int.Airport
(icao, iata, name, city, country, latitude, longitude, altitude,
timezone_name, timezone_delta, daylight_savings_time, type, source, _data_source, _load_time)
select icao, iata, airport_name, city, country, latitude, longitude, altitude, timezone_name,
        timezone_delta, daylight_savings_time, type, source, _data_source, _load_time
from air_travel_stg.airports
where country = 'United States'
and type in ('airport', NULL)
and icao in (select icao from air_travel_int.tmp_duplicate_icao)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [15]:
%%bigquery
select count(*) airports_us_only
from air_travel_int.Airport

Query is running:   0%|          |

Downloading:   0%|          |

airports_us_only
0              1531

In [16]:
%%bigquery
insert into air_travel_int.Airport
(icao, iata, name, city, country, latitude, longitude, altitude,
timezone_name, timezone_delta, daylight_savings_time, type, source, _data_source, _load_time)
select icao, iata, airport_name, city, country, latitude, longitude, altitude, timezone_name,
        timezone_delta, daylight_savings_time, type, source, _data_source, _load_time
from air_travel_stg.airports
where country != 'United States'
and type in ('airport', NULL)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [17]:
%%bigquery
select count(*) as airports_non_us
from air_travel_int.Airport
where country != 'United States'

Query is running:   0%|          |

Downloading:   0%|          |

airports_non_us
0             6512

In [18]:
%%bigquery
select count(*) as airports_total
from air_travel_int.Airport

Query is running:   0%|          |

Downloading:   0%|          |

airports_total
0            8043

##### Look at the records missing icao codes

In [19]:
%%bigquery
select * except(latitude, longitude, altitude, timezone_name, timezone_delta, daylight_savings_time, _data_source, _load_time)
from air_travel_int.Airport
where icao is null
order by name

Query is running:   0%|          |

Downloading:   0%|          |

icao  iata                             name          city state  \
0    None   AUE              Abu Rudeis Airport     Abu Rudeis  None   
1    None   ACU                 Achutupo Airport      Achutupo  None   
2    None   AIM                    Ailuk Airport  Ailuk Island  None   
3    None   AIC                    Airok Airport         Airok  None   
4    None  None  Airport - Rodalies de Catalunya       El Prat  None   
..    ...   ...                              ...           ...   ...   
283  None   LWE                 Wonopito Airport      Lewoleba  None   
284  None   WTO             Wotho Island Airport  Wotho Island  None   
285  None   SZI                   Zaysan Airport        Zaysan  None   
286  None  None                 Znamenka airport    Znamenskoe  None   
287  None  None   Zurich Airport Railway Station        Kloten  None   

              country     type source  
0               Egypt  airport   User  
1              Panama  airport   User  
2    Marshall Islands  airport   User  
3    Marshall Islands  airport   User  
4               Spain  airport   User  
..                ...      ...    ...  
283         Indonesia  airport   User  
284  Marshall Islands  airport   User  
285        Kazakhstan  airport   User  
286            Russia  airport   User  
287       Switzerland  airport   User  

[288 rows x 8 columns]

In [20]:
%%bigquery
select count(*) as missing_iata
from air_travel_int.Airport
where iata is null

Query is running:   0%|          |

Downloading:   0%|          |

missing_iata
0          1773

##### Call LLM
##### Use gemini to fill in the missing icao and other empty values in a record. Also, determine if the null and unknown records are real airports, want to remove them from the table if they aren't airports.

In [6]:
import vertexai
from vertexai.generative_models import GenerativeModel, Part

prompt = """Here is a list of ids and names.
I want you to check if the name corresponds to a real airport. If it does, return the original id and name along with the icao code, iata code, city, state or province, and country.
Return the results as json.
For example,
{"name": "Los Angeles International Airport": "icao": "KLAX", "iata": "LAX", "city": "Los Angelos", "state": "CA", "country": "United States"},
{"name": "Adak Airport": "icao": "PADK", "iata": "ADK", "city": "Adak Island", "state": "AK", "country": "United States"}
Don't return the records which are not valid airports.

Below is the list of names:
"Los Angeles International Airport, United States"
"Adak Airport, United States"
"TX Airport, United States"
"""

vertexai.init(project=project_id, location=region)
model = GenerativeModel(model_name)
resp = model.generate_content([prompt])
resp_text = resp.text.replace("```json", "").replace("```", "").replace("\n", "")
print(resp_text)

[  {    "name": "Los Angeles International Airport, United States",    "icao": "KLAX",    "iata": "LAX",    "city": "Los Angeles",    "state": "CA",    "country": "United States"  },  {    "name": "Adak Airport, United States",    "icao": "PADK",    "iata": "ADK",    "city": "Adak Island",    "state": "AK",    "country": "United States"  }]


##### Refine the prompt, adding instructions and making it more dynamic. Also, send small batches to the LLM to reduce hallucinations

In [21]:
import itertools, json, pandas, pandas_gbq
from google.cloud import bigquery
import vertexai
from vertexai.generative_models import GenerativeModel, Part

prompt = """Here is a list of names.
I want you to check if the name corresponds to a real airport. If it does, return the original name and country, along with the icao code, iata code, city, state or province, and country.
Return the results as a properly formatted json object with only one json object per line.
Return only one answer per airport.
Don't return the records which are not airports.
Don't return any empty json objects.
Don't return an explanation for your answer.
Here are some sample runs:

I pass you:
"Los Angeles International Airport, United States"
"Adak Airport, United States"
"TX Airport, United States"

You return:
{"name": "Los Angeles International Airport", "icao": "KLAX", "iata": "LAX", "city": "Los Angelos", "state": "CA", "country": "United States"}
{"name": "Adak Airport", "icao": "PADK", "iata": "ADK", "city": "Adak Island", "state": "AK", "country": "United States"}
"""
sql = """select distinct name, country from air_travel_int.Airport
where icao is null and name is not null and country is not null
"""

bq_client = bigquery.Client()
rows = bq_client.query_and_wait(sql)
vertexai.init(project=project_id, location=region)
model = GenerativeModel(model_name)

batch_size = 30    # send 30 airport names at a time
record_counter = 0
airport_str = ""
airports = []
for row in rows:
    record_counter += 1
    if record_counter == 1:
        airport_str = f"{row['name']},{row['country']}"
    else:
        airport_str += f"\n {row['name']},{row['country']}"

    if record_counter == batch_size:
        airports.append(airport_str)
        airport_str = ""
        record_counter = 0

print(f"{len(airports)} batches will be sent to LLM")
#print("airports are:", airports)

# send records to LLM and save results to the temp airports table
table_id = "air_travel_int.tmp_airports"

for i, records in enumerate(airports):
    first_airport = records.split(",")[0]
    print(f"{i}: batch starting with airport {first_airport}")

    resp = model.generate_content([records, prompt])
    resp_text = resp.text.replace("```json", "").replace("```", "")
    #print("resp_text:", resp_text)

    json_text = resp_text.split("\n")
    #print("json_text:", json_text)

    json_objs = []

    for json_str in json_text:
        if json_str in (None, ""):
            continue
        else:
            #print("json_str", json_str)
            json_str_clean = json_str.replace("},", "}")

            try:
                json_objs.append(json.loads(json_str))
            except Exception as e:
                print(f"Error converting {json_str} to json:", e)

    print("json_objs:", json_objs)

    try:
        df_raw = pandas.DataFrame(json_objs)
        #print("df_raw", df_raw.to_string())
    except Exception as e:
        print("Error while creating df_raw:", e)
        break

    try:
        df_unique = df_raw.drop_duplicates(subset=["name", "country"], keep="last")
        #print("df_unique", df_unique.to_string())
    except Exception as e:
        print("Error while creating df_unique:", e)
        break
        #print(f"got back {len(df_raw.index)} airports from LLM")

    try:
        if i == 0:
            pandas_gbq.to_gbq(df_unique, table_id, project_id=project_id, if_exists="replace")
        else:
            pandas_gbq.to_gbq(df_unique, table_id, project_id=project_id, if_exists="append")
        #print(f"saved results to {table_id}")
    except Exception as e:
        print("Error while writing to BQ:", e, "\n Error caused by: ", df_unique)


9 batches will be sent to LLM
0: batch starting with airport Ofu Airport
json_objs: [{'name': 'Ofu Airport', 'icao': 'NSAS', 'iata': 'OFU', 'city': 'Ofu Island', 'state': None, 'country': 'American Samoa'}, {'name': 'Catoca Airport', 'icao': 'FNCT', 'iata': None, 'city': 'Catoca', 'state': None, 'country': 'Angola'}, {'name': 'Bloomfield Airport', 'icao': 'YBOM', 'iata': 'BLO', 'city': 'Bloomfield', 'state': 'QLD', 'country': 'Australia'}, {'name': 'Byron Airport', 'icao': 'YBYR', 'iata': None, 'city': 'Byron Bay', 'state': 'NSW', 'country': 'Australia'}, {'name': 'Exmouth Airport', 'icao': 'YPEX', 'iata': 'EXM', 'city': 'Exmouth', 'state': 'WA', 'country': 'Australia'}, {'name': 'Morawa Airport', 'icao': 'YMRW', 'iata': 'MWB', 'city': 'Morawa', 'state': 'WA', 'country': 'Australia'}, {'name': 'Schofields Aerodrome', 'icao': 'YSCF', 'iata': None, 'city': 'Schofields', 'state': 'NSW', 'country': 'Australia'}, {'name': 'Bimini North Seaplane Base', 'icao': None, 'iata': 'NSB', 'city': 'A

100%|██████████| 1/1 [00:00<00:00, 5737.76it/s]


1: batch starting with airport High River Regional Airport
json_objs: [{'name': 'High River Regional Airport', 'icao': 'CFX8', 'iata': None, 'city': 'High River', 'state': 'AB', 'country': 'Canada'}, {'name': 'Olds Didsbury Airport', 'icao': 'CEA3', 'iata': None, 'city': 'Olds/Didsbury', 'state': 'AB', 'country': 'Canada'}, {'name': 'Albian Aerodrome', 'icao': 'CEL4', 'iata': None, 'city': 'Fort MacKay', 'state': 'AB', 'country': 'Canada'}, {'name': 'Sundre Airport', 'icao': 'CFN7', 'iata': None, 'city': 'Sundre', 'state': 'AB', 'country': 'Canada'}, {'name': 'Fort McMurray - Mildred Lake Airport', 'icao': 'CER4', 'iata': None, 'city': 'Mildred Lake', 'state': 'AB', 'country': 'Canada'}, {'name': 'Fox Harbour Airport', 'icao': 'CFH4', 'iata': 'YFX', 'city': 'Fox Harbour', 'state': 'NS', 'country': 'Canada'}, {'name': 'Sechelt Aerodrome', 'icao': 'CAP3', 'iata': None, 'city': 'Sechelt', 'state': 'BC', 'country': 'Canada'}, {'name': 'Qualicum Beach Airport', 'icao': 'CAT4', 'iata': 'XQU'

100%|██████████| 1/1 [00:00<00:00, 4471.54it/s]


2: batch starting with airport All Airports
json_objs: [{'name': 'Jing Gang Shan Airport', 'icao': 'ZSGS', 'iata': 'JGS', 'city': 'Jinggangshan', 'province': 'Jiangxi', 'country': 'China'}]
Error while writing to BQ: Reason: Provided Schema does not match Table cs329e-sp2025:air_travel_int.tmp_airports. Cannot add fields (field: province) 
 Error caused by:                       name  icao iata          city province country
0  Jing Gang Shan Airport  ZSGS  JGS  Jinggangshan  Jiangxi   China
3: batch starting with airport Huehuetenango Airport
json_objs: [{'name': 'Huehuetenango Airport', 'icao': 'MGHT', 'iata': 'HUG', 'city': 'Huehuetenango', 'state': 'Huehuetenango', 'country': 'Guatemala'}, {'name': 'Dibrugarh Airport', 'icao': 'VEMN', 'iata': 'DIB', 'city': 'Dibrugarh', 'state': 'Assam', 'country': 'India'}, {'name': 'Latur Airport', 'icao': 'VALT', 'iata': 'LTU', 'city': 'Latur', 'state': 'Maharashtra', 'country': 'India'}, {'name': 'Tuticorin Airport', 'icao': 'VOTK', 'iata': 'TC

...

100%|██████████| 1/1 [00:00<00:00, 8322.03it/s]


5: batch starting with airport Enejit Airport
json_objs: [{'name': 'Enejit Airport', 'icao': 'PKAE', 'iata': None, 'city': 'Enejit Island', 'state': None, 'country': 'Marshall Islands'}, {'name': 'Woja Airport', 'icao': 'PKWA', 'iata': 'WJA', 'city': 'Woja', 'state': None, 'country': 'Marshall Islands'}, {'name': 'Kaben Airport', 'icao': 'PKKN', 'iata': 'KBN', 'city': 'Kaben Island', 'state': None, 'country': 'Marshall Islands'}, {'name': 'Rongelap Island Airport', 'icao': 'PKRG', 'iata': 'RNP', 'city': 'Rongelap Island', 'state': None, 'country': 'Marshall Islands'}, {'name': 'Likiep Airport', 'icao': 'PKLK', 'iata': 'LIK', 'city': 'Likiep Island', 'state': None, 'country': 'Marshall Islands'}, {'name': 'Aur Island Airport', 'icao': 'PKAU', 'iata': 'AUL', 'city': 'Aur Island', 'state': None, 'country': 'Marshall Islands'}, {'name': 'Ebon Airport', 'icao': 'PKEO', 'iata': 'EBO', 'city': 'Ebon Island', 'state': None, 'country': 'Marshall Islands'}, {'name': 'Airok Airport', 'icao': 'PKA

100%|██████████| 1/1 [00:00<00:00, 6932.73it/s]


6: batch starting with airport Samjiyon Airport
json_objs: [{'name': 'Gardermoen Airport', 'icao': 'ENGM', 'iata': 'OSL', 'city': 'Oslo', 'province': 'Viken', 'country': 'Norway'}, {'name': 'Contadora Airport', 'icao': 'MPRA', 'iata': 'OTD', 'city': 'Contadora Island', 'province': 'Panama', 'country': 'Panama'}, {'name': 'Tubuala Airport', 'icao': 'MPYA', 'iata': 'TUW', 'city': 'Tubuala', 'province': 'Kuna Yala', 'country': 'Panama'}, {'name': 'Garachine Airport', 'icao': 'MPGN', 'iata': 'GHE', 'city': 'Garachine', 'province': 'Darién', 'country': 'Panama'}, {'name': 'Achutupo Airport', 'icao': 'MPAH', 'iata': 'ACU', 'city': 'Achutupo', 'province': 'Kuna Yala', 'country': 'Panama'}, {'name': 'EL Real Airport', 'icao': 'MPRU', 'iata': 'ELE', 'city': 'El Real de Santa Maria', 'province': 'Darién', 'country': 'Panama'}, {'name': 'Gasmata Island Airport', 'icao': 'AYGM', 'iata': 'GMI', 'city': 'Gasmata Island', 'province': 'West New Britain', 'country': 'Papua New Guinea'}, {'name': 'Obo A

100%|██████████| 1/1 [00:00<00:00, 8542.37it/s]


In [22]:
%%bigquery
select *
from air_travel_int.tmp_airports
order by name, country

Query is running:   0%|          |

Downloading:   0%|          |

name  icao  iata          city  \
0                      Ailuk Airport  PKLK   AIM  Ailuk Island   
1                      Airok Airport  PKAJ   AIC         Airok   
2    Akwa Ibom International Airport  DNAI   QUO           Uyo   
3                   Albian Aerodrome  CEL4  None   Fort MacKay   
4                 Algeciras Heliport  LEAG  None     Algeciras   
..                               ...   ...   ...           ...   
107                  Wenshan Airport  ZWWS   WNH       Wenshan   
108                     Woja Airport  PKWA   WJA          Woja   
109                 Wonopito Airport  WARA   WGP      Wonosobo   
110             Wotho Island Airport  PKWO   WTO  Wotho Island   
111                   Zaysan Airport  UASZ  none        Zaysan   

                      state           country  
0                      None  Marshall Islands  
1                      None  Marshall Islands  
2           Akwa Ibom State           Nigeria  
3                        AB            Canada  
4                      None             Spain  
..                      ...               ...  
107                      YN             China  
108                    None  Marshall Islands  
109            Central Java         Indonesia  
110                    None  Marshall Islands  
111  East Kazakhstan Region        Kazakhstan  

[112 rows x 6 columns]

##### Check for duplicate records

In [23]:
%%bigquery
  select name, country, count(*) as duplicates
  from air_travel_int.tmp_airports
  group by name, country
  having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [name, country, duplicates]
Index: []

##### Merge `tmp_airports` into `Airport` by joining on airport name and country.



In [24]:
%%bigquery
update air_travel_int.Airport a
set a.icao = t.icao, a.iata = t.iata, a.city = t.city, a.state = t.state
from air_travel_int.tmp_airports t
where a.name = t.name and a.country = t.country
and a.icao is null
and t.icao is not null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [25]:
%%bigquery
select * from air_travel_int.Airport
where icao is null

Query is running:   0%|          |

Downloading:   0%|          |

icao  iata                                        name           city  \
0    None  None  Billy Bishop Toronto City Airport Terminal        Toronto   
1    None   PVP                          Palo Verde Airport      San Bruno   
2    None   SSB          Christiansted Harbor Seaplane Base  Christiansted   
3    None   YTO                                All Airports        Toronto   
4    None   XBG                             Bogande Airport        Bogande   
..    ...   ...                                         ...            ...   
174  None   LSA                              Losuia Airport         Losuia   
175  None   OBX                                 Obo Airport            Obo   
176  None   UKU                                Nuku Airport           Nuku   
177  None   WPM                               Wipim Airport          Wipim   
178  None   TFM                           Telefomin Airport      Telefomin   

    state           country                                   latitude  \
0    None            Canada  43.63252300000000000000000000000000000000   
1    None            Mexico  27.09305600000000000000000000000000000000   
2    None    Virgin Islands  17.74722200000000000000000000000000000000   
3    None            Canada  43.65305600000000000000000000000000000000   
4    None            Canada  48.32949800000000000000000000000000000000   
..    ...               ...                                        ...   
174  None  Papua New Guinea  -8.50582000000000000000000000000000000000   
175  None  Papua New Guinea  -7.58300000000000000000000000000000000000   
176  None  Papua New Guinea  -3.66700000000000000000000000000000000000   
177  None  Papua New Guinea  -8.78822000000000000000000000000000000000   
178  None  Papua New Guinea  -5.11700000000000000000000000000000000000   

                                       longitude  altitude  \
0     -79.39634500000000000000000000000000000000       250   
1    -112.09888900000000000000000000000000000000        55   
2     -64.70500000000000000000000000000000000000         0   
3     -79.38305600000000000000000000000000000000       302   
4     -70.99569700000000000000000000000000000000       531   
..                                           ...       ...   
174   151.08100000000000000000000000000000000000        27   
175   141.31700000000000000000000000000000000000        29   
176   142.48300000000000000000000000000000000000       750   
177   142.88200000000000000000000000000000000000       173   
178   141.63300000000000000000000000000000000000         0   

            timezone_name  timezone_delta daylight_savings_time     type  \
0                    None              -5                     A  airport   
1        America/Mazatlan              -7                     A  airport   
2       America/St_Thomas              -4                     A  airport   
3         America/Toronto              -5                     A  airport   
4         America/Toronto              -5                     A  airport   
..                    ...             ...                   ...      ...   
174  Pacific/Port_Moresby              10                     U  airport   
175  Pacific/Port_Moresby              10                     U  airport   
176  Pacific/Port_Moresby              10                     U  airport   
177  Pacific/Port_Moresby              10                     U  airport   
178  Pacific/Port_Moresby              10                     U  airport   

    source _data_source                       _load_time  
0     User  openflights 2025-01-24 18:55:03.442905+00:00  
1     User  openflights 2025-01-24 18:55:03.442905+00:00  
2     User  openflights 2025-01-24 18:55:03.442905+00:00  
3     User  openflights 2025-01-24 18:55:03.442905+00:00  
4     User  openflights 2025-01-24 18:55:03.442905+00:00  
..     ...          ...                              ...  
174   User  openflights 2025-01-24 18:55:03.442905+00:00  
175   User  openflights 2025-01-24 18:55:03.44290

##### Delete records which are missing an icao code

In [26]:
%%bigquery
delete from air_travel_int.Airport
where icao is null or icao = ''

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check uniqueness of primary key field


In [27]:
%%bigquery
select icao, count(*) as duplicate_icao
from air_travel_int.Airport
group by icao
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

icao  duplicate_icao
0   CJT2               3
1   LEAG               3
2   CYML               2
3   VEMN               2
4   VCBI               2
5   VCCW               2
6   OIKQ               2
7   MZBZ               2
8   SBPP               2
9   TRPG               2
10  SCGZ               2
11  WBKK               2
12  DNAI               2
13  FNCT               2
14  EHLE               2
15  LFSB               2
16  LUBL               2
17  UKLU               2
18  HKKI               2
19  HKLE               2
20  FMMN               2
21  VRMH               2
22  UAAH               2
23  UASS               2
24  UASB               2
25  WIPH               2
26  WAOP               2
27  WARA               2
28  WBGF               2
29  WAAA               2
30  ZSNJ               2
31  ZYDQ               2
32  WAPP               2
33  RJBE               2
34  PKLK               2
35  PKWA               2
36  PKMA               2
37  PKMJ               2

In [28]:
%%bigquery
select * from air_travel_int.Airport
where icao in
    (select icao
      from air_travel_int.Airport
      group by icao
      having count(*) > 1)
order by icao

Query is running:   0%|          |

Downloading:   0%|          |

icao  iata                     name             city  state    country  \
0   CJT2  None  Matheson Island Airport  Matheson Island     MB     Canada   
1   CJT2  None  Matheson Island Airport  Matheson Island   None     Canada   
2   CJT2  None  Matheson Island Airport  Matheson Island     MB     Canada   
3   CYML   YML       Charlevoix Airport       Charlevoix   None     Canada   
4   CYML   YMP     Port McNeill Airport     Port McNeill     BC     Canada   
..   ...   ...                      ...              ...    ...        ...   
73  WIPH   KRC     Depati Parbo Airport          Kerinci  Jambi  Indonesia   
74  ZSNJ   NTG          Nantong Airport          Nantong     JS      China   
75  ZSNJ   NKG    Nanjing Lukou Airport          Nanjing   None      China   
76  ZYDQ   DQA    Daqing Saertu Airport           Daqing     HE      China   
77  ZYDQ   DQA           Saertu Airport           Daqing   None      China   

                                     latitude  \
0   51.73222200000000000000000000000000000000   
1   51.73220062255859400000000000000000000000   
2   51.73222200000000000000000000000000000000   
3   47.59749984741211000000000000000000000000   
4   50.57555600000000000000000000000000000000   
..                                        ...   
73   1.88107100000000000000000000000000000000   
74  32.07080000000000000000000000000000000000   
75  31.74200057983398400000000000000000000000   
76  46.58333300000000000000000000000000000000   
77  46.74638888890000000000000000000000000000   

                                      longitude  altitude      timezone_name  \
0    -96.93444400000000000000000000000000000000       725   America/Winnipeg   
1    -96.93440246582031000000000000000000000000       725   America/Winnipeg   
2    -96.93444400000000000000000000000000000000       725   America/Winnipeg   
3    -70.22389984130860000000000000000000000000       977               None   
4   -127.02861100000000000000000000000000000000       225  America/Vancouver   
..                                          ...       ...                ...   
73   101.44226100000000000000000000000000000000      2000       Asia/Jakarta   
74   120.97600000000000000000000000000000000000         0      Asia/Shanghai   
75   118.86199951171875000000000000000000000000        49      Asia/Shanghai   
76   125.00000000000000000000000000000000000000      1020      Asia/Shanghai   
77   125.14055555600000000000000000000000000000       496      Asia/Shanghai   

    timezone_delta daylight_savings_time     type       source _data_source  \
0               -6                     A  airport         User  openflights   
1               -6                     A  airport  OurAirports  openflights   
2               -6                     A  airport         User  openflights   
3             <NA>                    \N  airport  OurAirports  openflights   
4               -8                     A  airport         User  openflights   
..             ...                   ...      ...          ...          ...   
73               7                     U  airport         User  openflights   
74               8                     U  airport         User  openflights   
75               8                     U  airport  OurAirports  openflights   
76               8                     U  airport         User  openflights   
77               8                     N  airport  OurAirports  openflights   

                         _load_time  
0  2025-01-24 18:55:03.442905+00:00  
1  2025-01-24 18:55:03.442905+00:00  
2  2025-01-24 18:55:03.442905+00:00  
3  2025-01-24 18:55:03.442905+00:00  
4  2025-01-24 18:55:03.442905+00:00  
..                              ...  
73 2025-01-24 18:55:03.442905+00:00  
74 2025-01-24 18:55:03.442905+00:00  
75 2025-01-24 18:55:03.442905+00:00  
76 2025-01-24 18:55:03.442905+00:00  
77 2025-01-24 18:55:03.442905+00:00  

[78 rows x 16 columns]

##### Remove the duplicate records whose `source` = 'User' because these appear to be less trustworthy than those from `OurAirports`

---



In [29]:
%%bigquery
delete from air_travel_int.Airport
where source = 'User'
and icao in (select icao
             from air_travel_int.Airport
             group by icao
             having count(*) > 1)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [30]:
%%bigquery
select icao, count(*) as duplicate_icao
from air_travel_int.Airport
group by icao
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [icao, duplicate_icao]
Index: []

In [31]:
%%bigquery
select count(*) as airports_final_count
from air_travel_int.Airport

Query is running:   0%|          |

Downloading:   0%|          |

airports_final_count
0                  7822

#### Clean up

In [32]:
%%bigquery
drop table if exists air_travel_int.tmp_airports;
drop table if exists air_travel_int.tmp_duplicate_icao;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Now that we have a clean Airport table, we can create all the child tables that reference it. This will address criteria 9 (aka anomaly type 9).

#### `TSA_Traffic` table (criteria 9)

In [33]:
%%bigquery
select count(*) tsa_stg_records
from air_travel_stg.tsa_traffic

Query is running:   0%|          |

Downloading:   0%|          |

tsa_stg_records
0            10530

In [34]:
%%bigquery
select t.event_date, t.event_hour, a.icao, t.tsa_checkpoint, t.passenger_count
from air_travel_int.Airport a join air_travel_stg.tsa_traffic t
on a.iata = t.airport_code
where a.country = 'United States'

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour  icao tsa_checkpoint  passenger_count
0     2024-03-27          12  PADK    Checkpoint1                7
1     2024-05-08          12  PADK    Checkpoint1               23
2     2023-06-07          12  PADK    Checkpoint1                3
3     2024-07-24          13  PADK    Checkpoint1                1
4     2022-08-17          13  PADK    Checkpoint1               67
...          ...         ...   ...            ...              ...
9676  2024-07-17          13  KHTS  Main Terminal               34
9677  2024-07-31          13  KHTS  Main Terminal               25
9678  2023-06-21           6  KPKB           Main                5
9679  2024-01-24          12  KPKB           Main                4
9680  2023-06-14          12  KPKB           Main               10

[9681 rows x 5 columns]

In [36]:
%%bigquery
create or replace table air_travel_int.tmp_tsa_traffic as
    select distinct t.event_date, t.event_hour, a.icao as airport_icao, t.tsa_checkpoint, t.passenger_count,
      t._data_source, t._load_time
    from air_travel_int.Airport a join air_travel_stg.tsa_traffic t
    on a.iata = t.airport_code
    where a.country = 'United States'

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [37]:
%%bigquery
select * from air_travel_int.tmp_tsa_traffic

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao   tsa_checkpoint  passenger_count  \
0     2024-04-14           0         KALS  Alamosa Airport                0   
1     2024-04-14           0         KMTJ             MTJZ                0   
2     2024-04-14           0         KSMF        Central B               54   
3     2024-04-14           0         KTEX             TEXZ                0   
4     2024-04-14           0         KGJT             GJTZ                0   
...          ...         ...          ...              ...              ...   
9258  2022-09-07          12         PHNL            Mauka              848   
9259  2022-09-07          12         PHNL   CP 1 Lanes 3&4              129   
9260  2017-11-19           0         PHNL            HNL03               43   
9261  2017-11-19           0         PHNL            HNL03               11   
9262  2017-11-26           0         PHNL            HNL03                0   

     _data_source                       _load_time  
0        tsa-foia 2025-01-24 18:57:07.734242+00:00  
1        tsa-foia 2025-01-24 18:57:07.734242+00:00  
2        tsa-foia 2025-01-24 18:57:07.734242+00:00  
3        tsa-foia 2025-01-24 18:57:07.734242+00:00  
4        tsa-foia 2025-01-24 18:57:07.734242+00:00  
...           ...                              ...  
9258     tsa-foia 2025-01-24 19:04:21.290966+00:00  
9259     tsa-foia 2025-01-24 19:04:21.290966+00:00  
9260     tsa-foia 2025-01-24 19:04:25.128348+00:00  
9261     tsa-foia 2025-01-24 19:04:25.128348+00:00  
9262     tsa-foia 2025-01-24 19:04:33.067313+00:00  

[9263 rows x 7 columns]

##### Check for primary key fields for uniqueness

In [39]:
%%bigquery
select event_date, event_hour, airport_icao, tsa_checkpoint, count(*) as count
from air_travel_int.tmp_tsa_traffic
group by event_date, event_hour, airport_icao, tsa_checkpoint
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao   tsa_checkpoint  count
0    2023-12-27          14         KBOI         BOI-Ckpt     18
1    2023-12-27          14         KBNA      BNA Central     15
2    2024-03-17           0         KLAS       Term 1 - D      4
3    2017-11-26           0         KATL  Main Checkpoint      3
4    2017-11-26           0         KDEN            South      3
..          ...         ...          ...              ...    ...
513  2022-12-04           0         PHNL            HNL03      2
514  2023-02-19           0         PHNL            HNL03      2
515  2023-01-30           0         PHNL            HNL03      2
516  2023-07-16           0         PHNL            Makai      2
517  2017-11-19           0         PHNL            HNL03      2

[518 rows x 5 columns]

In [41]:
%%bigquery
select * from air_travel_int.tmp_tsa_traffic
where event_date = '2023-12-27'
and event_hour = 14
and airport_icao = 'KBOI'
and tsa_checkpoint = 'BOI-Ckpt'

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao tsa_checkpoint  passenger_count  \
0   2023-12-27          14         KBOI       BOI-Ckpt              111   
1   2023-12-27          14         KBOI       BOI-Ckpt              447   
2   2023-12-27          14         KBOI       BOI-Ckpt              511   
3   2023-12-27          14         KBOI       BOI-Ckpt              614   
4   2023-12-27          14         KBOI       BOI-Ckpt              125   
5   2023-12-27          14         KBOI       BOI-Ckpt              371   
6   2023-12-27          14         KBOI       BOI-Ckpt               58   
7   2023-12-27          14         KBOI       BOI-Ckpt               34   
8   2023-12-27          14         KBOI       BOI-Ckpt               63   
9   2023-12-27          14         KBOI       BOI-Ckpt              360   
10  2023-12-27          14         KBOI       BOI-Ckpt              720   
11  2023-12-27          14         KBOI       BOI-Ckpt                2   
12  2023-12-27          14         KBOI       BOI-Ckpt              266   
13  2023-12-27          14         KBOI       BOI-Ckpt              160   
14  2023-12-27          14         KBOI       BOI-Ckpt              514   
15  2023-12-27          14         KBOI       BOI-Ckpt              506   
16  2023-12-27          14         KBOI       BOI-Ckpt              368   
17  2023-12-27          14         KBOI       BOI-Ckpt               36   

   _data_source                       _load_time  
0      tsa-foia 2025-01-24 18:59:22.498508+00:00  
1      tsa-foia 2025-01-24 18:59:22.498508+00:00  
2      tsa-foia 2025-01-24 18:59:22.498508+00:00  
3      tsa-foia 2025-01-24 18:59:22.498508+00:00  
4      tsa-foia 2025-01-24 18:59:22.498508+00:00  
5      tsa-foia 2025-01-24 18:59:22.498508+00:00  
6      tsa-foia 2025-01-24 18:59:22.498508+00:00  
7      tsa-foia 2025-01-24 18:59:22.498508+00:00  
8      tsa-foia 2025-01-24 18:59:22.498508+00:00  
9      tsa-foia 2025-01-24 18:59:22.498508+00:00  
10     tsa-foia 2025-01-24 18:59:22.498508+00:00  
11     tsa-foia 2025-01-24 18:59:22.498508+00:00  
12     tsa-foia 2025-01-24 18:59:22.498508+00:00  
13     tsa-foia 2025-01-24 18:59:22.498508+00:00  
14     tsa-foia 2025-01-24 18:59:22.498508+00:00  
15     tsa-foia 2025-01-24 18:59:22.498508+00:00  
16     tsa-foia 2025-01-24 18:59:22.498508+00:00  
17     tsa-foia 2025-01-24 18:59:22.498508+00:00

##### Remove all duplicate records because passenger counts are inconsistent and numbers can't be trusted (would require manual work to verify which counts are accurate)

In [42]:
%%bigquery
create or replace table air_travel_int.tmp_duplicate_tsa_traffic as
    select * from air_travel_int.tmp_tsa_traffic
    where struct(event_date, event_hour, airport_icao, tsa_checkpoint) in
              (select struct(event_date, event_hour, airport_icao, tsa_checkpoint)
                from air_travel_int.tmp_tsa_traffic
                group by event_date, event_hour, airport_icao, tsa_checkpoint
                having count(*) > 1)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [43]:
%%bigquery
select * from air_travel_int.tmp_duplicate_tsa_traffic
order by event_date, event_hour, airport_icao, tsa_checkpoint

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao        tsa_checkpoint  \
0     2017-11-19           0         KATL       Main Checkpoint   
1     2017-11-19           0         KATL       Main Checkpoint   
2     2017-11-19           0         KDEN                 South   
3     2017-11-19           0         KDEN                 South   
4     2017-11-19           0         KDTW                 Red 3   
...          ...         ...          ...                   ...   
1032  2024-06-23           0         PAFA              ASAA-FAI   
1033  2024-06-23           0         PANC  F Arrival Checkpoint   
1034  2024-06-23           0         PANC  F Arrival Checkpoint   
1035  2024-06-23           0         PANC      South Checkpoint   
1036  2024-06-23           0         PANC      South Checkpoint   

      passenger_count _data_source                       _load_time  
0                  29     tsa-foia 2025-01-24 19:04:25.128348+00:00  
1                  18     tsa-foia 2025-01-24 19:04:25.128348+00:00  
2                  16     tsa-foia 2025-01-24 19:04:25.128348+00:00  
3                 134     tsa-foia 2025-01-24 19:04:25.128348+00:00  
4                  61     tsa-foia 2025-01-24 19:04:25.128348+00:00  
...               ...          ...                              ...  
1032              154     tsa-foia 2025-01-24 19:01:54.684687+00:00  
1033                6     tsa-foia 2025-01-24 19:01:54.684687+00:00  
1034                2     tsa-foia 2025-01-24 19:01:54.684687+00:00  
1035              202     tsa-foia 2025-01-24 19:01:54.684687+00:00  
1036              140     tsa-foia 2025-01-24 19:01:54.684687+00:00  

[1037 rows x 7 columns]

In [44]:
%%bigquery
select * from air_travel_int.tmp_tsa_traffic
except distinct
select * from air_travel_int.tmp_duplicate_tsa_traffic

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao  tsa_checkpoint  passenger_count  \
0     2024-04-17          12         KDRO      Checkpoint               82   
1     2024-04-17          12         KEUG            EUGZ              271   
2     2024-04-17          12         KFNT          AOO-01                0   
3     2024-04-17          12         KHPN   Main Terminal              330   
4     2024-04-17          12         KGEG         GEG-A/B              332   
...          ...         ...          ...             ...              ...   
8221  2023-10-11          13         PHNL           HNL04              478   
8222  2022-09-04           0         PHNL           HNL03               40   
8223  2022-09-07          12         PHNL           Mauka              848   
8224  2022-09-07          12         PHNL  CP 1 Lanes 3&4              129   
8225  2017-11-26           0         PHNL           HNL03                0   

     _data_source                       _load_time  
0        tsa-foia 2025-01-24 18:57:32.242204+00:00  
1        tsa-foia 2025-01-24 18:57:32.242204+00:00  
2        tsa-foia 2025-01-24 18:57:32.242204+00:00  
3        tsa-foia 2025-01-24 18:57:32.242204+00:00  
4        tsa-foia 2025-01-24 18:57:32.242204+00:00  
...           ...                              ...  
8221     tsa-foia 2025-01-24 19:04:14.654967+00:00  
8222     tsa-foia 2025-01-24 19:04:17.989859+00:00  
8223     tsa-foia 2025-01-24 19:04:21.290966+00:00  
8224     tsa-foia 2025-01-24 19:04:21.290966+00:00  
8225     tsa-foia 2025-01-24 19:04:33.067313+00:00  

[8226 rows x 7 columns]

In [45]:
%%bigquery
create or replace table air_travel_int.TSA_Traffic as
    (select * from air_travel_int.tmp_tsa_traffic
    except distinct
    select * from air_travel_int.tmp_duplicate_tsa_traffic)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Double-check uniqueness of primary key fields

In [46]:
%%bigquery
select event_date, event_hour, airport_icao, tsa_checkpoint, count(*) as count
from air_travel_int.TSA_Traffic
group by event_date, event_hour, airport_icao, tsa_checkpoint
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao            tsa_checkpoint  count
0   2023-03-12        <NA>         KATL           Main Checkpoint      2
1   2023-03-12        <NA>         KDCA               Concourse A      2
2   2023-03-12        <NA>         KDEN                     South      2
3   2023-03-12        <NA>         KEWR                   CKPT-A1      2
4   2023-03-12        <NA>         KFAT                    FAT 01      2
5   2023-03-12        <NA>         KIAD  Passenger Screening Area      2
6   2023-03-12        <NA>         KIND              Checkpoint A      2
7   2023-03-12        <NA>         KJFK                Terminal 1      2
8   2023-03-12        <NA>         KMIA                  South-J1      2
9   2023-03-12        <NA>         KMSP                  South CP      2
10  2023-03-12        <NA>         KONT                        T2      2
11  2023-03-12        <NA>         KORD                        4B      2
12  2023-03-12        <NA>         KPHX                     T-4 A      2
13  2023-03-12        <NA>         KPIT           Main Checkpoint      2
14  2023-03-12        <NA>         KSEA                     SCP 3      2
15  2023-03-12        <NA>         KSJC                Terminal A      2
16  2023-03-12        <NA>         PAFA                  ASAA-FAI      2
17  2023-03-12        <NA>         PANC          South Checkpoint      2

##### Delete all records which have a null event hour (as this is one of our primary key fields and is not supposed to be null)

In [47]:
%%bigquery
delete from air_travel_int.TSA_Traffic where event_hour is null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Recheck uniqueness of the primary key fields

In [48]:
%%bigquery
select event_date, event_hour, airport_icao, tsa_checkpoint, count(*) as count
from air_travel_int.TSA_Traffic
group by event_date, event_hour, airport_icao, tsa_checkpoint
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [event_date, event_hour, airport_icao, tsa_checkpoint, count]
Index: []

##### Check foreign key constraint (`airport_icao`)

In [49]:
%%bigquery
select count(*) as orphan_records
from air_travel_int.TSA_Traffic
where airport_icao not in (select icao from air_travel_int.Airport)

Query is running:   0%|          |

Downloading:   0%|          |

orphan_records
0               0

In [50]:
%%bigquery
select count(*) as final_count
from air_travel_int.TSA_Traffic

Query is running:   0%|          |

Downloading:   0%|          |

final_count
0         8000

##### Clean up

In [51]:
%%bigquery
drop table if exists air_travel_int.tmp_tsa_traffic;
drop table if exists air_travel_int.tmp_duplicate_tsa_traffic;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### `Airport_Review` table (data enrichment task)

###### Recreate table with icao as the airport identifier (in place of iata)

In [52]:
%%bigquery
select distinct r.id, r.thread_id, r.airport_code as icao, r.date_created, r.author,
  r.subject, r.body
from air_travel_stg.airport_reviews r join air_travel_int.Airport a
on a.icao = r.airport_code

Query is running:   0%|          |

Downloading:   0%|          |

id  thread_id  icao        date_created   author  \
0     21134      18493  AGGH 2015-08-18 06:08:46     None   
1      9233       7907  AYMH 2011-08-15 06:17:01     None   
2      5128        447  AYMN 2010-01-29 05:20:51     None   
3      8021        447  AYMN 2011-03-20 03:22:10     None   
4      5115        447  AYMN 2010-01-27 06:36:02     None   
...     ...        ...   ...                 ...      ...   
8686  82575      79931  MDSD 2020-05-09 13:52:15    zeina   
8687  82574      79930  RPLC 2020-05-09 13:52:08    zeina   
8688  20427      17786  RPLL 2014-11-18 03:27:53    zmrac   
8689  19573      16932  FKKD 2014-04-04 00:04:33     zone   
8690  84167      81494  MMPE 2022-02-18 22:37:05  zpaulca   

                                  subject  \
0                                 re: HIR   
1                    Still a good airport   
2                                 re: MDU   
3                                 re: MDU   
4                                 re: MDU   
...                                   ...   
8686  Bad credit is a big sin to mankind.   
8687  Bad credit is a big sin to mankind.   
8688                                 help   
8689                                scamm   
8690                    OPEN and GREAT!!!   

                                                   body  
0     Reply to @Ozguy: It really needs TLC. Yesterda...  
1                                 Still to many rascals  
2     Although I do not know Graham, I understand he...  
3     Good evening Sypho - remember when you threw t...  
4     Reply to @Ozguy: Greetings - I lived there in ...  
...                                                 ...  
8686  My credit cards debt kept me in a complete sta...  
8687  My credit cards debt kept me in a complete sta...  
8688  Sino po my alam na nag aasist sa airport? Tour...  
8689  oki so I ordered a sphinx cat and the lady had...  
8690  The easiest airport for quick, friendly AOE pr...  

[8691 rows x 7 columns]

##### Materialize to a temp table

In [54]:
%%bigquery
create or replace table air_travel_int.tmp_airport_reviews as
    select distinct r.id, r.thread_id, r.airport_code as icao, r.date_created, r.author,
        r.subject, r.body, r._data_source, r._load_time
    from air_travel_stg.airport_reviews r join air_travel_int.Airport a
    on a.icao = r.airport_code

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Determine which reviews are about airports and detect their sentiment

In [55]:
%%bigquery
select subject, body from air_travel_int.tmp_airport_reviews
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

subject  \
0                      re: HIR   
1  What is it actually called?   
2         Still a good airport   
3                      re: MDU   
4                      re: MDU   
5                      re: MDU   
6                      re: MDU   
7                      re: MDU   
8                          POM   
9         One day soon I hope.   

                                                body  
0  Reply to @Ozguy: It really needs TLC. Yesterda...  
1  What is the specific name of the Denali Airpor...  
2                              Still to many rascals  
3  Although I do not know Graham, I understand he...  
4  Understand that  one John Rutter is still in t...  
5  Reply to @Ozguy: Greetings - I lived there in ...  
6  Syphers G C & L A(07) 5445 7968 268 Obi Obi Rd...  
7  Good evening Sypho - remember when you threw t...  
8  A reasonable international terminal but nothin...  
9  Having spent 2 years living in Rabaul when I w...

In [56]:
import json
import pandas, pandas_gbq
import vertexai
from vertexai.generative_models import GenerativeModel, Part
from google.cloud import bigquery

prompt = """Go through this list of reviews and determine which ones refer to an airport.
If the review refers to an airport, return relevant = True, otherwise return relevant = False.
Also, detect the tone of the review. Return positive, neutral or negative based on the sentiment.
Return the id along with the relevancy and sentiment for each one.
Format the results as a list of json objects with the schema:
[{id:integer, relevant:boolean, sentiment:string}]
Do not include an explanation with your answer.
"""
llm_input_sql = "select id, subject, body from air_travel_int.tmp_airport_reviews limit 50"

full_table_sql = "select * from air_travel_int.tmp_airport_reviews"


def do_inference(input_str):

    vertexai.init(project=project_id, location=region)
    model = GenerativeModel(model_name)
    resp = model.generate_content([input_str, prompt])
    #print("resp:", resp)
    resp_text = resp.text.replace("```json", "").replace("```", "").replace("\n", "")
    print("resp_text:", resp_text)

    results = json.loads(resp_text)

    return results


bq_client = bigquery.Client()
rows = bq_client.query_and_wait(llm_input_sql)

batch_size = 50
reviews = [] # for storing the inputs to LLM
results = [] # for storing the outputs from LLM
combined_results = []

for i, row in enumerate(rows):

    review_str = f"id={row['id']}, subject={row['subject']}, body={row['body']}"
    reviews.append(review_str)

    if i > 0 and i % batch_size == 0:
        # process batch
        print("processing batch")
        reviews_str = '\n'.join(reviews)
        results = do_inference(reviews_str)
        combined_results.extend(results)

        # empty out smaller list before processing next batch
        reviews = []

if len(reviews) > 0:
    print("processing last batch")
    reviews_str = '\n'.join(reviews)
    results = do_inference(reviews_str)
    combined_results.extend(results)

print("combined_results:", combined_results)

df = pandas.DataFrame(combined_results)
print("df:", df.to_string())

table_id = "air_travel_int.tmp_airport_reviews_analyzed" # output table
pandas_gbq.to_gbq(df, table_id, project_id=project_id, if_exists="replace")

processing last batch
resp_text: [  {"id": 21134, "relevant": true, "sentiment": "negative"},  {"id": 3896, "relevant": true, "sentiment": "neutral"},  {"id": 9233, "relevant": true, "sentiment": "negative"},  {"id": 5128, "relevant": false, "sentiment": "neutral"},  {"id": 7500, "relevant": false, "sentiment": "neutral"},  {"id": 5115, "relevant": false, "sentiment": "positive"},  {"id": 6614, "relevant": false, "sentiment": "neutral"},  {"id": 8021, "relevant": false, "sentiment": "positive"},  {"id": 18055, "relevant": true, "sentiment": "negative"},  {"id": 16709, "relevant": true, "sentiment": "positive"},  {"id": 3922, "relevant": true, "sentiment": "positive"},  {"id": 17609, "relevant": true, "sentiment": "positive"},  {"id": 17099, "relevant": true, "sentiment": "positive"},  {"id": 22256, "relevant": true, "sentiment": "negative"},  {"id": 8367, "relevant": true, "sentiment": "neutral"},  {"id": 16249, "relevant": true, "sentiment": "negative"},  {"id": 16189, "relevant": fal

100%|██████████| 1/1 [00:00<00:00, 5753.50it/s]


##### Join the two tables to inspect the LLM-generated results

In [58]:
%%bigquery
select r.id, r.subject, r.body, a.relevant, a.sentiment, r._data_source, r._load_time
from air_travel_int.tmp_airport_reviews r
join air_travel_int.tmp_airport_reviews_analyzed a
on r.id = a.id

Query is running:   0%|          |

Downloading:   0%|          |

id                                            subject  \
0   21134                                            re: HIR   
1    3896                        What is it actually called?   
2    9233                               Still a good airport   
3    5128                                            re: MDU   
4    7500                                            re: MDU   
5    5115                                            re: MDU   
6    6614                                            re: MDU   
7    8021                                            re: MDU   
8   18055                                                POM   
9   16709                               One day soon I hope.   
10   3922                                       re: Akureryi   
11  17609                                        KEF airport   
12  17099                                                 Hi   
13  22256                                       ZNA location   
14   8367                          Flights to Powell River ?   
15  16249                                     Incorrect link   
16  16189                                   re: nice airport   
17  19923                          Airport user for 20 years   
18  20486  Short Sighted Municipality - Closing this airp...   
19  20757                              This is a total shame   
20  20222                                          Dangerous   
21   5205                                     re: Ice Runway   
22  16204                                      Wind Turbines   
23  17497                                      Wind Turbines   
24  17335                                  re: Wind Turbines   
25  17619                                  Dunnville Airport   
26  18214                                       Crop dusters   
27  10864                               re: Self serve 100LL   
28  17252                                   Self serve 100LL   
29  22896                        Fuel Prices 100LL and Jet A   
30  29597                                        Fuel Prices   
31  21953                         100 ll June 2016 fuel 1.25   
32  45318                          Self Serve 100LL and JetA   
33  20903                                         Fuel Price   
34  20621                                         Fuel price   
35   9550                                   Self serve 100LL   
36  79510                                        Fuel Prices   
37  35438                                    Self Serve Fuel   
38  19708                                   Self serve 100LL   
39  29443                                        Fuel Prices   
40  18799                               re: Self serve 100LL   
41   8646  pilot rental    sea plane to remote fishing lodge   
42    398                                              trees   
43  22969  122.8 is local floatplane frequency and Kenora...   
44  22968  Seaplane base is across from hospital, not whe...   
45  27021                                       (no subject)   
46  10700                           re: Great Place to Visit   
47    905                                       A bit old...   
48  25431                                    What did I see?   
49  10021                           Nice Friendly Airport !!   

                                                 body  relevant sentiment  \
0   Reply to @Ozguy: It really needs TLC. Yesterda...      True  negative   
1   What is the specific name of the Denali Airpor...      True   neutral   
2                               Still to many rascals      True  negative   
3   Although I do not know Graham, I understand he...     False   neutral   
4   Understand that  one John Rutter is still in t...     False   neutral   
5   Reply to @Ozguy: Greetings - I lived there in ...     False  positive   
6   Syphers G C & L A(07) 5445 7968 268 Obi Obi Rd...     False   neutral   
7   Good evening Sypho - remember when you threw t...     False  positive   
8   A reasonable international terminal but nothi

##### Configure safety settings, add exception handling, and analyze the full table (8691 records), using a larger batch size.

In [60]:
import json
import pandas, pandas_gbq
from google.cloud import bigquery
import vertexai
from vertexai.generative_models import (
    GenerativeModel,
    HarmCategory,
    HarmBlockThreshold,
    Part,
    SafetySetting,
)

prompt = """Go through this list of reviews and determine which ones refer to an airport.
If the review refers to an airport, return relevant = True, otherwise return relevant = False.
Also, detect the tone of the review. Return positive, neutral or negative based on the sentiment.
Return the id along with the relevancy and sentiment for each one.
Format the results as a list of json objects with the schema:
[{id:integer, relevant:boolean, sentiment:string}]
Do not include an explanation with your answer.
"""
llm_input_sql = "select id, subject, body from air_travel_int.tmp_airport_reviews order by id"

vertexai.init(project=project_id, location=region)
model = GenerativeModel(model_name)

safety_config = [
    SafetySetting(
        category=HarmCategory.HARM_CATEGORY_DANGEROUS_CONTENT,
        threshold=HarmBlockThreshold.BLOCK_ONLY_HIGH,
    ),
]

def do_inference(input_str):

    results = []

    resp = model.generate_content([input_str, prompt], safety_settings=safety_config)
    prompt_token_count = resp.usage_metadata.prompt_token_count
    candidate_token_count = resp.usage_metadata.candidates_token_count

    #print("prompt token count:", prompt_token_count)
    #print("candidates token count:", candidate_token_count)

    if candidate_token_count == 0 or candidate_token_count == 8192: # 8192 is the output token limit
        # skip this batch because response is either null or truncated
        return results

    resp_text = resp.text.replace("```json", "").replace("```", "").replace("\n", "")
    #print("resp_text:", resp_text)

    try:
        results = json.loads(resp_text)
    except Exception as e:
        print(f"Error converting {resp_text} to json:", e)

    return results

batch_size = 250
start_batch_counter = 0
reviews = [] # for storing the inputs to LLM
results = [] # for storing the outputs from LLM
combined_results = []

bq_client = bigquery.Client()
rows = bq_client.query_and_wait(llm_input_sql)

for i, row in enumerate(rows):

    review_str = f"id={row['id']}, subject={row['subject']}, body={row['body']}"
    reviews.append(review_str)

    if i > 0 and i % batch_size == 0:
        # process batch
        print(f"processing records {start_batch_counter} - {i}")
        reviews_str = '\n'.join(reviews)
        results = do_inference(reviews_str)

        if len(results) > 0:
            combined_results.extend(results)

        # empty out smaller list before processing next batch
        reviews = []
        start_batch_counter = i + 1

if len(reviews) > 0:
    print(f"processing last batch, starting with record {start_batch_counter}")
    reviews_str = '\n'.join(reviews)
    results = do_inference(reviews_str)

    if len(results) > 0:
        combined_results.extend(results)
        reviews = []

print("combined_results:", len(combined_results), "records")

df = pandas.DataFrame(combined_results)
#print("df:", df.to_string())

table_id = "air_travel_int.tmp_airport_reviews_analyzed" # output table
pandas_gbq.to_gbq(df, table_id, project_id=project_id, if_exists="replace")

processing records 0 - 250
processing records 251 - 500
processing records 501 - 750
processing records 751 - 1000
processing records 1001 - 1250
processing records 1251 - 1500
processing records 1501 - 1750
processing records 1751 - 2000
processing records 2001 - 2250
processing records 2251 - 2500
processing records 2501 - 2750
processing records 2751 - 3000
processing records 3001 - 3250
processing records 3251 - 3500
processing records 3501 - 3750
processing records 3751 - 4000
processing records 4001 - 4250
processing records 4251 - 4500
processing records 4501 - 4750
processing records 4751 - 5000
processing records 5001 - 5250
processing records 5251 - 5500
processing records 5501 - 5750
processing records 5751 - 6000
processing records 6001 - 6250
Error converting [  {    "id": 23022,    "relevant": true,    "sentiment": "negative"  },  {    "id": 23034,    "relevant": true,    "sentiment": "neutral"  },  {    "id": 23036,    "relevant": true,    "sentiment": "negative"  },  { 

100%|██████████| 1/1 [00:00<00:00, 8422.30it/s]


In [61]:
%%bigquery
select r.id, r.subject, r.body, a.relevant, a.sentiment
from air_travel_int.tmp_airport_reviews r
join air_travel_int.tmp_airport_reviews_analyzed a
on r.id = a.id

Query is running:   0%|          |

Downloading:   0%|          |

id                                  subject  \
0        398                                    trees   
1         11                            Wind turbines   
2        303                                   runway   
3        359                                 The Wind   
4        316                          MROC/SJO Flying   
...      ...                                      ...   
5436   39711                                  Awesome   
5437  507394                        all hail TUSAŞ ;)   
5438  504644          Friendly staff and good pricing   
5439    8879  Fabulous Museum - Best in South America   
5440   84167                        OPEN and GREAT!!!   

                                                   body  relevant sentiment  
0     big trees at north end. Most jets cannot make ...      True   warning  
1     If you're a pilot, watch for the wind turbines...      True   warning  
2     good but subject to crosswinds also seasonal  ...      True   warning  
3     Windy as hell. Make sure to tighten up your ba...      True   warning  
4     Get your flying out of the way in the mornings...      True   warning  
...                                                 ...       ...       ...  
5436                   Agreed with what @Komatoast said     False  positive  
5437  This is the runway where Turkish Fighter-X wil...      True  positive  
5438  Staff are informative and friendly, easygoing ...      True  positive  
5439  Better known as Campo dos Afonsas home to Braz...     False  positive  
5440  The easiest airport for quick, friendly AOE pr...      True  positive  

[5441 rows x 5 columns]

##### Create the final table

In [62]:
%%bigquery
create or replace table air_travel_int.Airport_Review as
    select r.id, r.thread_id, r.icao, r.date_created, r.author, r.subject, r.body, a.relevant, a.sentiment,
      r._data_source, r._load_time
    from air_travel_int.tmp_airport_reviews r
    left join air_travel_int.tmp_airport_reviews_analyzed a
    on r.id = a.id

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [63]:
%%bigquery
select icao, sentiment, count(*) as count
from air_travel_int.Airport_Review
where relevant = True
group by icao, sentiment
order by count(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

icao sentiment  count
0     RPLL   neutral     67
1     RPLL  negative     38
2     FAOR  negative     30
3     LPBJ   neutral     25
4     RPLL  positive     20
...    ...       ...    ...
2134  KTEB   warning      1
2135  KBID   warning      1
2136  CYSP   warning      1
2137  PASO   warning      1
2138  CFH4   warning      1

[2139 rows x 3 columns]

##### Check uniqueness of primary key field

In [64]:
%%bigquery
select id, count(*) as duplicate_id
from air_travel_int.Airport_Review
group by id
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [id, duplicate_id]
Index: []

##### Check for foreign key violations

In [65]:
%%bigquery
select count(*) as orphan_records
from air_travel_int.Airport_Review
where icao not in (select icao from air_travel_int.Airport)

Query is running:   0%|          |

Downloading:   0%|          |

orphan_records
0               0

In [66]:
%%bigquery
select count(*) as airport_reviews_final_count
from air_travel_int.Airport_Review

Query is running:   0%|          |

Downloading:   0%|          |

airport_reviews_final_count
0                         8691

##### Clean up

In [67]:
%%bigquery
drop table if exists air_travel_int.tmp_airport_reviews;
drop table if exists air_travel_int.tmp_airport_reviews_analyzed;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### Create `Airport_Businesses`, `Business`, and `Menu_Items` tables (criteria 8, 9, and 10)

##### Decompose `airport_businesses` into `Business` and `Airport_Businesses`. This resolves anomaly type 10.

In [1]:
%%bigquery
select * from air_travel_stg.airport_businesses

Query is running:   0%|          |

Downloading:   0%|          |

airport_code terminal           business        category  \
0             abq        1        Video Phone   Phone Service   
1             abq        1   Vending Machines         Vending   
2             crw        1  Travel with Carie   Travel Agency   
3             sfo        2          Yoga Room         Fitness   
4             sfo        2          The Scoop  Ice Cream Shop   
...           ...      ...                ...             ...   
1569          gsp        2                ATM           other   
1570          gsp        2   Charging Station           other   
1571          gsp        2   Charging Station           other   
1572          gsp        2           Fuel Rod           other   
1573          gsp        2           Pharmacy           other   

                location                      menu_items  _data_source  \
0     Baggage Claim Area                            None  airportguide   
1     Baggage Claim Area                            None  airportguide   
2            Concourse A                            None  airportguide   
3            Concourse D                            None  airportguide   
4            Concourse D  Ice Cream,Frozen Yogurt,Shakes  airportguide   
...                  ...                             ...           ...   
1569                  A3                            None  airportguide   
1570                  A4                            None  airportguide   
1571                  A7                            None  airportguide   
1572                  A8                            None  airportguide   
1573                  A9                            None  airportguide   

                           _load_time  
0    2025-01-24 18:51:53.320638+00:00  
1    2025-01-24 18:51:53.320638+00:00  
2    2025-01-24 18:51:53.320638+00:00  
3    2025-01-24 18:51:53.320638+00:00  
4    2025-01-24 18:51:53.320638+00:00  
...                               ...  
1569 2025-01-24 18:51:53.320638+00:00  
1570 2025-01-24 18:51:53.320638+00:00  
1571 2025-01-24 18:51:53.320638+00:00  
1572 2025-01-24 18:51:53.320638+00:00  
1573 2025-01-24 18:51:53.320638+00:00  

[1574 rows x 8 columns]

##### Remove some of the noise by getting rid of the unwanted records; things like ticketing, baggage claim, car rental, restrooms, etc.

In [2]:
%%bigquery
select category, business, count(*) as num_businesses
from air_travel_stg.airport_businesses
where category not in ('Ticketing', 'Airlines', 'Airline', 'Airport Services', 'Car Rental', 'Cargo Services', 'Baggage Service', 'Baggage Services', 'Services', 'Air Transportation', 'Airline Ticketing', 'Security', 'Management', 'Airline Services', 'Customer Service', 'Administration', 'Other', 'Vacant', 'Government Services', 'Mail Services', 'Airport Security', 'Immigration', 'Information', 'Parking', 'Police Services', 'Public Space', 'Restrooms', 'Seating', 'Observation Point')
and business not in ('Restaurant', 'Restaurant Pre-Security', 'Restaurant Post-Security', 'Drinking Water', 'Food & Beverage', 'Restaurant-Bar', 'Snacks and drinks')
group by category, business
order by count(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

category       business  num_businesses
0      Newsstand    Hudson News              14
1       Shopping    Hudson News              13
2    Coffee Shop      Starbucks              12
3         Dining      Starbucks              11
4       Shopping      Gift Shop               6
..           ...            ...             ...
915       dining    Burger King               1
916        other     Escape Pod               1
917        other  Premium Sound               1
918        other            ATM               1
919        other       Pharmacy               1

[920 rows x 3 columns]

##### Create the junction table (anomaly type 9)

In [3]:
%%bigquery
select distinct a.icao, b.terminal, b.business, b.location
from air_travel_stg.airport_businesses b join air_travel_int.Airport a
on upper(b.airport_code) = a.iata
where a.country = 'United States'
and category not in ('Ticketing', 'Airlines', 'Airline', 'Airport Services', 'Car Rental', 'Cargo Services', 'Baggage Service', 'Baggage Services', 'Services', 'Air Transportation', 'Airline Ticketing', 'Security', 'Management', 'Airline Services', 'Customer Service', 'Administration', 'Other', 'Vacant', 'Government Services', 'Mail Services', 'Airport Security', 'Immigration', 'Information', 'Parking', 'Police Services', 'Public Space', 'Restrooms', 'Seating', 'Observation Point')
and business not in ('Restaurant', 'Restaurant Pre-Security', 'Restaurant Post-Security', 'Drinking Water', 'Food & Beverage', 'Restaurant-Bar', 'Snacks and drinks')
order by b.business

Query is running:   0%|          |

Downloading:   0%|          |

icao       terminal                    business                location
0     KPSP              1    12th Fairway Bar & Grill                 Gate 11
1     KBOI              1   13th Street Pub and Grill  Near gates B15 and B17
2     KPIE              1  3 Daughters Brewing at PIE                  Gate 2
3     KSFO              2              49 Mile Market             Concourse D
4     KLGB              1                    4th Vine           Near Gates G2
...    ...            ...                         ...                     ...
1090  KLAS              1                      iCandy      Terminal 1 Level 1
1091  KSFO              1                      iStore      Near Gates B2 - B4
1092  KBDL              1                      iStore             Gates 15-16
1093  KHOU              1                      iStore               Gates 1-4
1094  KLAX  international             iStore Boutique           Near Gate 136

[1095 rows x 4 columns]

In [4]:
%%bigquery
create or replace table air_travel_int.Airport_Businesses as
    select distinct a.icao, b.terminal, b.business, b.location
    from air_travel_stg.airport_businesses b join air_travel_int.Airport a
    on upper(b.airport_code) = a.iata
    where a.country = 'United States'
    and category not in ('Ticketing', 'Airlines', 'Airline', 'Airport Services', 'Car Rental', 'Cargo Services', 'Baggage Service', 'Baggage Services', 'Services', 'Air Transportation', 'Airline Ticketing', 'Security', 'Management', 'Airline Services', 'Customer Service', 'Administration', 'Other', 'Vacant', 'Government Services', 'Mail Services', 'Airport Security', 'Immigration', 'Information', 'Parking', 'Police Services', 'Public Space', 'Restrooms', 'Seating', 'Observation Point')
    and business not in ('Restaurant', 'Restaurant Pre-Security', 'Restaurant Post-Security', 'Drinking Water', 'Food & Beverage', 'Restaurant-Bar', 'Snacks and drinks')
    order by b.business

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check uniqueness of primary key fields in the junction table

In [5]:
%%bigquery
select icao, terminal, business, location, count(*) as count
from air_travel_int.Airport_Businesses
group by icao, terminal, business, location
order by count(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

icao       terminal                    business                location  \
0     KPSP              1    12th Fairway Bar & Grill                 Gate 11   
1     KBOI              1   13th Street Pub and Grill  Near gates B15 and B17   
2     KPIE              1  3 Daughters Brewing at PIE                  Gate 2   
3     KSFO              2              49 Mile Market             Concourse D   
4     KLGB              1                    4th Vine           Near Gates G2   
...    ...            ...                         ...                     ...   
1090  KLAS              1                      iCandy      Terminal 1 Level 1   
1091  KSFO              1                      iStore      Near Gates B2 - B4   
1092  KHOU              1                      iStore               Gates 1-4   
1093  KBDL              1                      iStore             Gates 15-16   
1094  KLAX  international             iStore Boutique           Near Gate 136   

      count  
0         1  
1         1  
2         1  
3         1  
4         1  
...     ...  
1090      1  
1091      1  
1092      1  
1093      1  
1094      1  

[1095 rows x 5 columns]

In [6]:
%%bigquery
select count(*) as final_count
from air_travel_int.Airport_Businesses

Query is running:   0%|          |

Downloading:   0%|          |

final_count
0         1095

##### Create new Business entity from `air_travel_stg.airport_businesses`

In [10]:
%%bigquery
select distinct business as name, category, menu_items, _data_source, _load_time
from air_travel_stg.airport_businesses
where category not in ('Ticketing', 'Airlines', 'Airline', 'Airport Services', 'Car Rental', 'Cargo Services', 'Baggage Service', 'Baggage Services', 'Services', 'Air Transportation', 'Airline Ticketing', 'Security', 'Management', 'Airline Services', 'Customer Service', 'Administration', 'Other', 'Vacant', 'Government Services', 'Mail Services', 'Airport Security', 'Immigration', 'Information', 'Parking', 'Police Services', 'Public Space', 'Restrooms', 'Seating', 'Observation Point')
and business not in ('Restaurant', 'Restaurant Pre-Security', 'Restaurant Post-Security', 'Drinking Water', 'Food & Beverage', 'Restaurant-Bar', 'Snacks and drinks')
order by category, business

Query is running:   0%|          |

Downloading:   0%|          |

name          category  \
0                                 ATM               ATM   
1                      Alaska Offices    Airline Office   
2                       Delta Offices    Airline Office   
3                         Airport MFE  Airport Facility   
4                             Gallery               Art   
..                                ...               ...   
967  Sky Lounge Steakhouse and Rawbar        restaurant   
968                            Police          security   
969                             Fedex  shipping company   
970                               UPS  shipping company   
971            Lanai City Service Inc    transportation   

                menu_items  _data_source                       _load_time  
0                     None  airportguide 2025-01-24 18:51:53.320638+00:00  
1                     None  airportguide 2025-01-24 18:51:53.320638+00:00  
2                     None  airportguide 2025-01-24 18:51:53.320638+00:00  
3                     None  airportguide 2025-01-24 18:51:53.320638+00:00  
4                     None  airportguide 2025-01-24 18:51:53.320638+00:00  
..                     ...           ...                              ...  
967  Steak,Seafood,Raw Bar  airportguide 2025-01-24 18:51:53.320638+00:00  
968                   None  airportguide 2025-01-24 18:51:53.320638+00:00  
969                   None  airportguide 2025-01-24 18:51:53.320638+00:00  
970                   None  airportguide 2025-01-24 18:51:53.320638+00:00  
971                   None  airportguide 2025-01-24 18:51:53.320638+00:00  

[972 rows x 5 columns]

In [9]:
%%bigquery
create or replace table air_travel_int.tmp_business as
    select distinct business as name, category, menu_items, _data_source, _load_time
    from air_travel_stg.airport_businesses
    where category not in ('Ticketing', 'Airlines', 'Airline', 'Airport Services', 'Car Rental', 'Cargo Services', 'Baggage Service', 'Baggage Services', 'Services', 'Air Transportation', 'Airline Ticketing', 'Security', 'Management', 'Airline Services', 'Customer Service', 'Administration', 'Other', 'Vacant', 'Government Services', 'Mail Services', 'Airport Security', 'Immigration', 'Information', 'Parking', 'Police Services', 'Public Space', 'Restrooms', 'Seating', 'Observation Point')
    and business not in ('Restaurant', 'Restaurant Pre-Security', 'Restaurant Post-Security', 'Drinking Water', 'Food & Beverage', 'Restaurant-Bar', 'Snacks and drinks')
    order by business

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check for uniqueness of primary key field, `name`

In [11]:
%%bigquery
select distinct name, count(*) as num_duplicates
from air_travel_int.tmp_business
group by name
having count(*) > 1
order by num_duplicates desc

Query is running:   0%|          |

Downloading:   0%|          |

name  num_duplicates
0               Starbucks              15
1             Burger King               6
2   Einstein Bros. Bagels               6
3                     ATM               5
4           Auntie Anne's               5
..                    ...             ...
80                   Vino               2
81                Wendy's               2
82  Wolfgang Puck Express               2
83        World Duty Free               2
84              Yoga Room               2

[85 rows x 2 columns]

In [12]:
%%bigquery
select *
from air_travel_int.tmp_business
where name = 'Starbucks'

Query is running:   0%|          |

Downloading:   0%|          |

name     category                                         menu_items  \
0   Starbucks  Coffee Shop                          Latte,Cappuccino,Espresso   
1   Starbucks  Coffee Shop                         Latte,Frappuccino,Espresso   
2   Starbucks  Coffee Shop      Caffè Americano,Caramel Macchiato,Frappuccino   
3   Starbucks  Coffee Shop                                Coffee,Tea,Pastries   
4   Starbucks  Coffee Shop          Caramel Macchiato,Iced Coffee,Frappuccino   
5   Starbucks  Coffee Shop                         Latte,Espresso,Frappuccino   
6   Starbucks  Coffee Shop                           Latte,Frappuccino,Muffin   
7   Starbucks  Coffee Shop  Caramel Macchiato,Pumpkin Spice Latte,Chai Tea...   
8   Starbucks       Dining                         Latte,Frappuccino,Pastries   
9   Starbucks       Dining                                Coffee,Tea,Pastries   
10  Starbucks       Dining                       Latte,Cappuccino,Frappuccino   
11  Starbucks       Dining                          Latte,Cappuccino,Espresso   
12  Starbucks       Dining                         Coffee,Pastries,Sandwiches   
13  Starbucks       Dining  Caramel Macchiato,Pumpkin Spice Latte,Frappuccino   
14  Starbucks       dining                         Coffee,Pastries,Sandwiches   

    _data_source                       _load_time  
0   airportguide 2025-01-24 18:51:53.320638+00:00  
1   airportguide 2025-01-24 18:51:53.320638+00:00  
2   airportguide 2025-01-24 18:51:53.320638+00:00  
3   airportguide 2025-01-24 18:51:53.320638+00:00  
4   airportguide 2025-01-24 18:51:53.320638+00:00  
5   airportguide 2025-01-24 18:51:53.320638+00:00  
6   airportguide 2025-01-24 18:51:53.320638+00:00  
7   airportguide 2025-01-24 18:51:53.320638+00:00  
8   airportguide 2025-01-24 18:51:53.320638+00:00  
9   airportguide 2025-01-24 18:51:53.320638+00:00  
10  airportguide 2025-01-24 18:51:53.320638+00:00  
11  airportguide 2025-01-24 18:51:53.320638+00:00  
12  airportguide 2025-01-24 18:51:53.320638+00:00  
13  airportguide 2025-01-24 18:51:53.320638+00:00  
14  airportguide 2025-01-24 18:51:53.320638+00:00

In [13]:
%%bigquery
select * from air_travel_int.tmp_business
where name = 'Burger King'

Query is running:   0%|          |

Downloading:   0%|          |

name   category                          menu_items  _data_source  \
0  Burger King     Dining  Whopper,French Fries,Chicken Fries  airportguide   
1  Burger King     Dining   Whoppers,Chicken Sandwiches,Fries  airportguide   
2  Burger King     Dining       Whopper,Fries,Chicken Nuggets  airportguide   
3  Burger King  Fast Food       Whopper,Fries,Chicken Nuggets  airportguide   
4  Burger King  Fast Food   Whopper,Chicken Fries,Onion Rings  airportguide   
5  Burger King     dining   Whopper,Chicken Fries,Onion Rings  airportguide   

                        _load_time  
0 2025-01-24 18:51:53.320638+00:00  
1 2025-01-24 18:51:53.320638+00:00  
2 2025-01-24 18:51:53.320638+00:00  
3 2025-01-24 18:51:53.320638+00:00  
4 2025-01-24 18:51:53.320638+00:00  
5 2025-01-24 18:51:53.320638+00:00

##### Rank by category and menu items in order to remove duplicate businesses

In [14]:
%%bigquery
with sorted_names as
    (select name, category, count(*) as num_businesses
    from air_travel_int.tmp_business
    group by name, category)
select row_number() over (partition by name order by (select num_businesses from sorted_names s where b. category = s.category and b.name = s.name) desc, length(menu_items) desc) AS rank, *
from air_travel_int.tmp_business b
where name in ('Starbucks', 'Burger King')
and menu_items is not null
order by name;

Query is running:   0%|          |

Downloading:   0%|          |

rank         name     category  \
0      1  Burger King       Dining   
1      2  Burger King       Dining   
2      3  Burger King       Dining   
3      4  Burger King    Fast Food   
4      5  Burger King    Fast Food   
5      6  Burger King       dining   
6      1    Starbucks  Coffee Shop   
7      2    Starbucks  Coffee Shop   
8      3    Starbucks  Coffee Shop   
9      4    Starbucks  Coffee Shop   
10     5    Starbucks  Coffee Shop   
11     6    Starbucks  Coffee Shop   
12     7    Starbucks  Coffee Shop   
13     8    Starbucks  Coffee Shop   
14     9    Starbucks       Dining   
15    10    Starbucks       Dining   
16    11    Starbucks       Dining   
17    12    Starbucks       Dining   
18    13    Starbucks       Dining   
19    14    Starbucks       Dining   
20    15    Starbucks       dining   

                                           menu_items  _data_source  \
0                  Whopper,French Fries,Chicken Fries  airportguide   
1                   Whoppers,Chicken Sandwiches,Fries  airportguide   
2                       Whopper,Fries,Chicken Nuggets  airportguide   
3                   Whopper,Chicken Fries,Onion Rings  airportguide   
4                       Whopper,Fries,Chicken Nuggets  airportguide   
5                   Whopper,Chicken Fries,Onion Rings  airportguide   
6   Caramel Macchiato,Pumpkin Spice Latte,Chai Tea...  airportguide   
7       Caffè Americano,Caramel Macchiato,Frappuccino  airportguide   
8           Caramel Macchiato,Iced Coffee,Frappuccino  airportguide   
9                          Latte,Frappuccino,Espresso  airportguide   
10                         Latte,Espresso,Frappuccino  airportguide   
11                          Latte,Cappuccino,Espresso  airportguide   
12                           Latte,Frappuccino,Muffin  airportguide   
13                                Coffee,Tea,Pastries  airportguide   
14  Caramel Macchiato,Pumpkin Spice Latte,Frappuccino  airportguide   
15                       Latte,Cappuccino,Frappuccino  airportguide   
16                         Latte,Frappuccino,Pastries  airportguide   
17                         Coffee,Pastries,Sandwiches  airportguide   
18                          Latte,Cappuccino,Espresso  airportguide   
19                                Coffee,Tea,Pastries  airportguide   
20                         Coffee,Pastries,Sandwiches  airportguide   

                         _load_time  
0  2025-01-24 18:51:53.320638+00:00  
1  2025-01-24 18:51:53.320638+00:00  
2  2025-01-24 18:51:53.320638+00:00  
3  2025-01-24 18:51:53.320638+00:00  
4  2025-01-24 18:51:53.320638+00:00  
5  2025-01-24 18:51:53.320638+00:00  
6  2025-01-24 18:51:53.320638+00:00  
7  2025-01-24 18:51:53.320638+00:00  
8  2025-01-24 18:51:53.320638+00:00  
9  2025-01-24 18:51:53.320638+00:00  
10 2025-01-24 18:51:53.320638+00:00  
11 2025-01-24 18:51:53.320638+00:00  
12 2025-01-24 18:51:53.320638+00:00  
13 2025-01-24 18:51:53.320638+00:00  
14 2025-01-24 18:51:53.320638+00:00  
15 2025-01-24 18:51:53.320638+00:00  
16 2025-01-24 18:51:53.320638+00:00  
17 2025-01-24 18:51:53.320638+00:00  
18 2025-01-24 18:51:53.320638+00:00  
19 2025-01-24 18:51:53.320638+00:00  
20 2025-01-24 18:51:53.320638+00:00

##### Materialize results to another temp table

In [15]:
%%bigquery
create or replace table air_travel_int.tmp_business_ranked as
    with sorted_categories as
        (select name, category, count(*) as num_businesses
        from air_travel_int.tmp_business
        group by name, category)
    select row_number() over (partition by name order by (select num_businesses from sorted_categories s where b. category = s.category and b.name = s.name) desc, length(menu_items) desc) AS rank, *
    from air_travel_int.tmp_business b
    where menu_items is not null
    order by name;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Rank the remaining records, the ones which don't have any menu items. Use the popularity of each category to determine the rankings

In [16]:
%%bigquery
select * from air_travel_int.tmp_business
where name in
    (select name
    from air_travel_int.tmp_business
    where menu_items is null
    group by name
    having count(*) > 1)
order by name, category
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

name            category menu_items  _data_source  \
0                    AED           Emergency       None  airportguide   
1                    AED             Medical       None  airportguide   
2                    ATM                 ATM       None  airportguide   
3                    ATM             Banking       None  airportguide   
4                    ATM           Financial       None  airportguide   
5                    ATM  Financial Services       None  airportguide   
6                    ATM               other       None  airportguide   
7              Book Soup           Bookstore       None  airportguide   
8              Book Soup            Shopping       None  airportguide   
9  Brighton Collectibles           Gift Shop       None  airportguide   

                        _load_time  
0 2025-01-24 18:51:53.320638+00:00  
1 2025-01-24 18:51:53.320638+00:00  
2 2025-01-24 18:51:53.320638+00:00  
3 2025-01-24 18:51:53.320638+00:00  
4 2025-01-24 18:51:53.320638+00:00  
5 2025-01-24 18:51:53.320638+00:00  
6 2025-01-24 18:51:53.320638+00:00  
7 2025-01-24 18:51:53.320638+00:00  
8 2025-01-24 18:51:53.320638+00:00  
9 2025-01-24 18:51:53.320638+00:00

In [20]:
%%bigquery
with sorted_categories as
    (select category, count(*) as num_businesses
    from air_travel_int.tmp_business
    group by category)

select row_number() over (partition by name order by (select num_businesses from sorted_categories s where b. category = s.category) desc) AS rank, *
FROM air_travel_int.tmp_business b
where menu_items is null
and name in ('Book Soup', 'Brighton Collectibles', 'Brookstone', 'Food Court')
order by name;

Query is running:   0%|          |

Downloading:   0%|          |

rank                   name           category menu_items  _data_source  \
0     1              Book Soup           Shopping       None  airportguide   
1     2              Book Soup          Bookstore       None  airportguide   
2     1  Brighton Collectibles           Shopping       None  airportguide   
3     2  Brighton Collectibles          Gift Shop       None  airportguide   
4     3  Brighton Collectibles            Jewelry       None  airportguide   
5     1             Brookstone           Shopping       None  airportguide   
6     2             Brookstone  Electronics Store       None  airportguide   
7     1             Food Court             Dining       None  airportguide   
8     2             Food Court             dining       None  airportguide   
9     3             Food Court         Food Court       None  airportguide   

                        _load_time  
0 2025-01-24 18:51:53.320638+00:00  
1 2025-01-24 18:51:53.320638+00:00  
2 2025-01-24 18:51:53.320638+00:00  
3 2025-01-24 18:51:53.320638+00:00  
4 2025-01-24 18:51:53.320638+00:00  
5 2025-01-24 18:51:53.320638+00:00  
6 2025-01-24 18:51:53.320638+00:00  
7 2025-01-24 18:51:53.320638+00:00  
8 2025-01-24 18:51:53.320638+00:00  
9 2025-01-24 18:51:53.320638+00:00

In [21]:
%%bigquery
insert into air_travel_int.tmp_business_ranked
with sorted_categories as
    (select category, count(*) as num_businesses
    from air_travel_int.tmp_business
    group by category)

select row_number() over (partition by name order by (select num_businesses from sorted_categories s where b. category = s.category) desc) AS rank, *
from air_travel_int.tmp_business b
where menu_items is null
and name not in (select name from air_travel_int.tmp_business_ranked);

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [22]:
%%bigquery
select * from air_travel_int.tmp_business_ranked
where name in ('Hudson News', 'Food Court')
order by name

Query is running:   0%|          |

Downloading:   0%|          |

rank         name           category menu_items  _data_source  \
0     1   Food Court             Dining       None  airportguide   
1     2   Food Court             dining       None  airportguide   
2     3   Food Court         Food Court       None  airportguide   
3     1  Hudson News           Shopping       None  airportguide   
4     2  Hudson News          Newsstand       None  airportguide   
5     3  Hudson News  Convenience Store       None  airportguide   

                        _load_time  
0 2025-01-24 18:51:53.320638+00:00  
1 2025-01-24 18:51:53.320638+00:00  
2 2025-01-24 18:51:53.320638+00:00  
3 2025-01-24 18:51:53.320638+00:00  
4 2025-01-24 18:51:53.320638+00:00  
5 2025-01-24 18:51:53.320638+00:00

##### Check uniqueness of primary key field (`name`)

In [23]:
%%bigquery
select name, count(*) as count
from air_travel_int.tmp_business_ranked
where rank = 1
group by name
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [name, count]
Index: []

##### Create the final table

In [24]:
%%bigquery
create or replace table air_travel_int.Business as
    select * except(rank)
    from air_travel_int.tmp_business_ranked
    where rank = 1

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [25]:
%%bigquery
select * from air_travel_int.Business

Query is running:   0%|          |

Downloading:   0%|          |

name    category  \
0                  Asian Street Eats       Asian   
1             La Provence Patisserie      Bakery   
2         Dogpatch Bakehouse & Caffè      Bakery   
3    The Great American Bagel Bakery      Bakery   
4                  Vanilla Bake Shop      Bakery   
..                               ...         ...   
826       Earl Campbell's Taco Truck      Dining   
827                      Tacos Locos      Dining   
828             The Peached Tortilla      Dining   
829                         Loteria!      Dining   
830           Jose Cuervo Tequileria  Restaurant   

                                    menu_items  _data_source  \
0                           Pad Thai,Sushi,Pho  airportguide   
1         Croissants,Macarons,Pain au Chocolat  airportguide   
2                   Pastries,Coffee,Sandwiches  airportguide   
3    Everything Bagel,Plain Bagel,Sesame Bagel  airportguide   
4                       Cookies,Cakes,Brownies  airportguide   
..                                         ...           ...   
826                 Tacos,Quesadillas,Burritos  airportguide   
827                 Tacos,Quesadillas,Burritos  airportguide   
828                 Tacos,Quesadillas,Burritos  airportguide   
829                 Tacos,Quesadillas,Burritos  airportguide   
830                 Tacos,Quesadillas,Burritos  airportguide   

                          _load_time  
0   2025-01-24 18:51:53.320638+00:00  
1   2025-01-24 18:51:53.320638+00:00  
2   2025-01-24 18:51:53.320638+00:00  
3   2025-01-24 18:51:53.320638+00:00  
4   2025-01-24 18:51:53.320638+00:00  
..                               ...  
826 2025-01-24 18:51:53.320638+00:00  
827 2025-01-24 18:51:53.320638+00:00  
828 2025-01-24 18:51:53.320638+00:00  
829 2025-01-24 18:51:53.320638+00:00  
830 2025-01-24 18:51:53.320638+00:00  

[831 rows x 5 columns]

In [26]:
%%bigquery
select count(*) as final_count
from air_travel_int.Business

Query is running:   0%|          |

Downloading:   0%|          |

final_count
0          831

##### Clean up

In [27]:
%%bigquery
drop table air_travel_int.tmp_business;
drop table air_travel_int.tmp_business_ranked;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Add a new `dining<BOOL>` field

In [33]:
%%bigquery
create or replace table air_travel_int.Business (name STRING,
    category STRING, dining BOOLEAN, menu_items STRING, _data_source STRING, _load_time TIMESTAMP)
    as select name, category, NULL, menu_items, _data_source, _load_time
    from air_travel_int.Business

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [34]:
%%bigquery
update air_travel_int.Business
    set dining = True where menu_items is not null;
update air_travel_int.Business
    set dining = False where menu_items is null;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [35]:
%%bigquery
select * from air_travel_int.Business
order by name

Query is running:   0%|          |

Downloading:   0%|          |

name           category  dining  \
0      12th Fairway Bar & Grill         Restaurant    True   
1     13th Street Pub and Grill             Dining    True   
2    3 Daughters Brewing at PIE             Dining    True   
3                49 Mile Market           Shopping   False   
4                      4th Vine         Restaurant    True   
..                          ...                ...     ...   
826          Zoom Travel Stores           Shopping   False   
827                      eSavvy  Electronics Store   False   
828                      iCandy        Candy Store   False   
829                      iStore           Shopping   False   
830             iStore Boutique        Electronics   False   

                                menu_items  _data_source  \
0                Sandwiches,Salads,Burgers  airportguide   
1    Pub Burger,Fish & Chips,Chicken Wings  airportguide   
2                       IPA,Stout,Pale Ale  airportguide   
3                                     None  airportguide   
4      Wine,Cheese Plate,Charcuterie Board  airportguide   
..                                     ...           ...   
826                                   None  airportguide   
827                                   None  airportguide   
828                                   None  airportguide   
829                                   None  airportguide   
830                                   None  airportguide   

                          _load_time  
0   2025-01-24 18:51:53.320638+00:00  
1   2025-01-24 18:51:53.320638+00:00  
2   2025-01-24 18:51:53.320638+00:00  
3   2025-01-24 18:51:53.320638+00:00  
4   2025-01-24 18:51:53.320638+00:00  
..                               ...  
826 2025-01-24 18:51:53.320638+00:00  
827 2025-01-24 18:51:53.320638+00:00  
828 2025-01-24 18:51:53.320638+00:00  
829 2025-01-24 18:51:53.320638+00:00  
830 2025-01-24 18:51:53.320638+00:00  

[831 rows x 6 columns]

##### Convert `menu_items` into an array of strings (anomaly type 8)

In [36]:
%%bigquery
select name, category, menu_items, split(menu_items, ',') as menu_items_array
from air_travel_int.Business
where dining = True

Query is running:   0%|          |

Downloading:   0%|          |

name    category  \
0                  Asian Street Eats       Asian   
1                  Vanilla Bake Shop      Bakery   
2    The Great American Bagel Bakery      Bakery   
3             La Provence Patisserie      Bakery   
4                Sweet Jill's Bakery      Bakery   
..                               ...         ...   
412       Earl Campbell's Taco Truck      Dining   
413             The Peached Tortilla      Dining   
414                         Loteria!      Dining   
415                      Tacos Locos      Dining   
416           Jose Cuervo Tequileria  Restaurant   

                                    menu_items  \
0                           Pad Thai,Sushi,Pho   
1                       Cookies,Cakes,Brownies   
2    Everything Bagel,Plain Bagel,Sesame Bagel   
3         Croissants,Macarons,Pain au Chocolat   
4                  Croissants,Muffins,Pastries   
..                                         ...   
412                 Tacos,Quesadillas,Burritos   
413                 Tacos,Quesadillas,Burritos   
414                 Tacos,Quesadillas,Burritos   
415                 Tacos,Quesadillas,Burritos   
416                 Tacos,Quesadillas,Burritos   

                                  menu_items_array  
0                           [Pad Thai, Sushi, Pho]  
1                       [Cookies, Cakes, Brownies]  
2    [Everything Bagel, Plain Bagel, Sesame Bagel]  
3         [Croissants, Macarons, Pain au Chocolat]  
4                  [Croissants, Muffins, Pastries]  
..                                             ...  
412                 [Tacos, Quesadillas, Burritos]  
413                 [Tacos, Quesadillas, Burritos]  
414                 [Tacos, Quesadillas, Burritos]  
415                 [Tacos, Quesadillas, Burritos]  
416                 [Tacos, Quesadillas, Burritos]  

[417 rows x 4 columns]

In [39]:
%%bigquery
with menu_items as (select name as business_name, split(menu_items, ',') as menu_items_array, _data_source, _load_time
                    from air_travel_int.Business
                    where dining = True)
select business_name, menu_item, _data_source, _load_time
from menu_items, unnest(menu_items_array) as menu_item

Query is running:   0%|          |

Downloading:   0%|          |

business_name    menu_item  _data_source  \
0          Asian Street Eats     Pad Thai  airportguide   
1          Asian Street Eats        Sushi  airportguide   
2          Asian Street Eats          Pho  airportguide   
3          Vanilla Bake Shop      Cookies  airportguide   
4          Vanilla Bake Shop        Cakes  airportguide   
...                      ...          ...           ...   
1246             Tacos Locos  Quesadillas  airportguide   
1247             Tacos Locos     Burritos  airportguide   
1248  Jose Cuervo Tequileria        Tacos  airportguide   
1249  Jose Cuervo Tequileria  Quesadillas  airportguide   
1250  Jose Cuervo Tequileria     Burritos  airportguide   

                           _load_time  
0    2025-01-24 18:51:53.320638+00:00  
1    2025-01-24 18:51:53.320638+00:00  
2    2025-01-24 18:51:53.320638+00:00  
3    2025-01-24 18:51:53.320638+00:00  
4    2025-01-24 18:51:53.320638+00:00  
...                               ...  
1246 2025-01-24 18:51:53.320638+00:00  
1247 2025-01-24 18:51:53.320638+00:00  
1248 2025-01-24 18:51:53.320638+00:00  
1249 2025-01-24 18:51:53.320638+00:00  
1250 2025-01-24 18:51:53.320638+00:00  

[1251 rows x 4 columns]

##### Create the final table

In [40]:
%%bigquery
create or replace table air_travel_int.Menu_Items as
    with menu_items as (select name as business_name, split(menu_items, ',') as menu_items_array, _data_source, _load_time
                    from air_travel_int.Business
                    where dining = True)
    select business_name, menu_item, _data_source, _load_time
    from menu_items, unnest(menu_items_array) as menu_item

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [41]:
%%bigquery
select * from air_travel_int.Menu_Items
order by business_name

Query is running:   0%|          |

Downloading:   0%|          |

business_name      menu_item  _data_source  \
0      12th Fairway Bar & Grill     Sandwiches  airportguide   
1      12th Fairway Bar & Grill         Salads  airportguide   
2      12th Fairway Bar & Grill        Burgers  airportguide   
3     13th Street Pub and Grill     Pub Burger  airportguide   
4     13th Street Pub and Grill  Chicken Wings  airportguide   
...                         ...            ...           ...   
1246                Zocalo Cafe          Tacos  airportguide   
1247                Zocalo Cafe       Burritos  airportguide   
1248                Zona Fresca          Tacos  airportguide   
1249                Zona Fresca    Quesadillas  airportguide   
1250                Zona Fresca       Burritos  airportguide   

                           _load_time  
0    2025-01-24 18:51:53.320638+00:00  
1    2025-01-24 18:51:53.320638+00:00  
2    2025-01-24 18:51:53.320638+00:00  
3    2025-01-24 18:51:53.320638+00:00  
4    2025-01-24 18:51:53.320638+00:00  
...                               ...  
1246 2025-01-24 18:51:53.320638+00:00  
1247 2025-01-24 18:51:53.320638+00:00  
1248 2025-01-24 18:51:53.320638+00:00  
1249 2025-01-24 18:51:53.320638+00:00  
1250 2025-01-24 18:51:53.320638+00:00  

[1251 rows x 4 columns]

##### Check for uniqueness of primary key fields (`business_name`, `menu_item`)

In [42]:
%%bigquery
select business_name, menu_item, count(*) as count
from air_travel_int.Menu_Items
group by business_name, menu_item
having count(*) > 1
order by business_name

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [business_name, menu_item, count]
Index: []

##### Remove the menu_items field from the `Business` table

In [43]:
%%bigquery
alter table air_travel_int.Business
    drop column menu_items

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [44]:
%%bigquery
select * from air_travel_int.Business

Query is running:   0%|          |

Downloading:   0%|          |

name    category  dining  _data_source  \
0                  Asian Street Eats       Asian    True  airportguide   
1                  Vanilla Bake Shop      Bakery    True  airportguide   
2    The Great American Bagel Bakery      Bakery    True  airportguide   
3             La Provence Patisserie      Bakery    True  airportguide   
4                Sweet Jill's Bakery      Bakery    True  airportguide   
..                               ...         ...     ...           ...   
826       Earl Campbell's Taco Truck      Dining    True  airportguide   
827             The Peached Tortilla      Dining    True  airportguide   
828                         Loteria!      Dining    True  airportguide   
829                      Tacos Locos      Dining    True  airportguide   
830           Jose Cuervo Tequileria  Restaurant    True  airportguide   

                          _load_time  
0   2025-01-24 18:51:53.320638+00:00  
1   2025-01-24 18:51:53.320638+00:00  
2   2025-01-24 18:51:53.320638+00:00  
3   2025-01-24 18:51:53.320638+00:00  
4   2025-01-24 18:51:53.320638+00:00  
..                               ...  
826 2025-01-24 18:51:53.320638+00:00  
827 2025-01-24 18:51:53.320638+00:00  
828 2025-01-24 18:51:53.320638+00:00  
829 2025-01-24 18:51:53.320638+00:00  
830 2025-01-24 18:51:53.320638+00:00  

[831 rows x 5 columns]

In [45]:
%%bigquery
select * from air_travel_int.Menu_Items
order by business_name

Query is running:   0%|          |

Downloading:   0%|          |

business_name      menu_item  _data_source  \
0      12th Fairway Bar & Grill     Sandwiches  airportguide   
1      12th Fairway Bar & Grill         Salads  airportguide   
2      12th Fairway Bar & Grill        Burgers  airportguide   
3     13th Street Pub and Grill     Pub Burger  airportguide   
4     13th Street Pub and Grill  Chicken Wings  airportguide   
...                         ...            ...           ...   
1246                Zocalo Cafe          Tacos  airportguide   
1247                Zocalo Cafe       Burritos  airportguide   
1248                Zona Fresca          Tacos  airportguide   
1249                Zona Fresca    Quesadillas  airportguide   
1250                Zona Fresca       Burritos  airportguide   

                           _load_time  
0    2025-01-24 18:51:53.320638+00:00  
1    2025-01-24 18:51:53.320638+00:00  
2    2025-01-24 18:51:53.320638+00:00  
3    2025-01-24 18:51:53.320638+00:00  
4    2025-01-24 18:51:53.320638+00:00  
...                               ...  
1246 2025-01-24 18:51:53.320638+00:00  
1247 2025-01-24 18:51:53.320638+00:00  
1248 2025-01-24 18:51:53.320638+00:00  
1249 2025-01-24 18:51:53.320638+00:00  
1250 2025-01-24 18:51:53.320638+00:00  

[1251 rows x 4 columns]

In [46]:
%%bigquery
select count(*) as final_count
from air_travel_int.Menu_Items

Query is running:   0%|          |

Downloading:   0%|          |

final_count
0         1251

#### Create `Country`

In [47]:
%%bigquery
select * from air_travel_stg.countries
order by name

Query is running:   0%|          |

Downloading:   0%|          |

name iso_code dafif_code _data_source  \
0                  Afghanistan       AF         AF  openflights   
1                      Albania       AL         AL  openflights   
2                      Algeria       DZ         AG  openflights   
3               American Samoa       AS         AQ  openflights   
4                       Angola       AO         AO  openflights   
..                         ...      ...        ...          ...   
256  Wallis and Futuna Islands       WF         WF  openflights   
257             Western Sahara       EH         WI  openflights   
258                      Yemen       YE         YM  openflights   
259                     Zambia       ZM         ZA  openflights   
260                   Zimbabwe       ZW         ZI  openflights   

                          _load_time  
0   2025-01-24 18:55:09.949985+00:00  
1   2025-01-24 18:55:09.949985+00:00  
2   2025-01-24 18:55:09.949985+00:00  
3   2025-01-24 18:55:09.949985+00:00  
4   2025-01-24 18:55:09.949985+00:00  
..                               ...  
256 2025-01-24 18:55:09.949985+00:00  
257 2025-01-24 18:55:09.949985+00:00  
258 2025-01-24 18:55:09.949985+00:00  
259 2025-01-24 18:55:09.949985+00:00  
260 2025-01-24 18:55:09.949985+00:00  

[261 rows x 5 columns]

##### Check uniqueness of primary key field

In [48]:
%%bigquery
select name, count(*) as count
from air_travel_stg.countries
group by name
having count(*) > 1
order by name

Query is running:   0%|          |

Downloading:   0%|          |

name  count
0      India      2
1  Palestine      2

In [49]:
%%bigquery
select * from air_travel_stg.countries
where name in ('India', 'Palestine')

Query is running:   0%|          |

Downloading:   0%|          |

name iso_code dafif_code _data_source                       _load_time
0      India       IN         IN  openflights 2025-01-24 18:55:09.949985+00:00
1      India       IN         BS  openflights 2025-01-24 18:55:09.949985+00:00
2  Palestine       PS         WE  openflights 2025-01-24 18:55:09.949985+00:00
3  Palestine       PS         GZ  openflights 2025-01-24 18:55:09.949985+00:00

##### Turn `dafif_code` into an array type, so that we can get rid of the duplicate records for India and Palestine

In [50]:
%%bigquery
select name, iso_code, array_agg(dafif_code) as dafif_codes
from air_travel_stg.countries
group by name, iso_code;

Executing query with job ID: f5a1f86c-e46e-4eb0-b65b-c3b3457841a7
Query executing: 0.30s


ERROR:
 400 Array cannot have a null element; error in writing field dafif_codes; reason: invalidQuery, location: query, message: Array cannot have a null element; error in writing field dafif_codes

Location: us-central1
Job ID: f5a1f86c-e46e-4eb0-b65b-c3b3457841a7



In [51]:
%%bigquery
select name, iso_code, array_agg(ifnull(dafif_code, 'Unknown')) as dafif_codes
from air_travel_stg.countries
where name in ('India', 'Palestine') or dafif_code is null
group by name, iso_code;

Query is running:   0%|          |

Downloading:   0%|          |

name iso_code dafif_codes
0  Bonaire, Saint Eustatius and Saba       BQ   [Unknown]
1                              India       IN    [IN, BS]
2                          Palestine       PS    [WE, GZ]

##### Create the final table

In [53]:
%%bigquery
create or replace table air_travel_int.Country as
    select name, iso_code, array_agg(ifnull(dafif_code, 'Unknown')) as dafif_codes, _data_source, _load_time
    from air_travel_stg.countries
    group by name, iso_code, _data_source, _load_time;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check uniqueness of primary key field (`name`)

In [54]:
%%bigquery
select name, count(*) as count
from air_travel_int.Country
group by name
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [name, count]
Index: []

In [55]:
%%bigquery
select count(*) as final_count
from air_travel_int.Country

Query is running:   0%|          |

Downloading:   0%|          |

final_count
0          259

#### `Airline` table

In [56]:
%%bigquery
select * from air_travel_stg.airlines
where country is not null

Query is running:   0%|          |

Downloading:   0%|          |

id                       name alias  iata icao      callsign  \
0     3577           Nada Air Service  None  None  NHZ      NADA AIR   
1     4316     Sahel Aviation Service  None  None  SAO        SAVSER   
2       62                   Air Togo  None    YT  TGA      AIR TOGO   
3      752                 Aerocardal  None  None  CDA        CARDAL   
4     2727  Helicopteros Agroforestal  None  None  HAA  AGROFORESTAL   
...    ...                        ...   ...   ...  ...           ...   
6139  1213                 Air Salone  None    20  RNE    AIR SALONE   
6140  2456           Freedom Airlines  None  None  FRL   FREEDOM AIR   
6141  3466              Mesa Airlines  None    YV  ASH   AIR SHUTTLE   
6142   492              Air Southwest  None  None  WOW       SWALLOW   
6143  1308               Airlines PNG  None    CG  TOK         BALUS   

               country  active _data_source                       _load_time  
0                 Chad   False  openflights 2025-01-24 18:52:44.140187+00:00  
1                 Mali   False  openflights 2025-01-24 18:52:44.140187+00:00  
2                 Togo   False  openflights 2025-01-24 18:52:44.140187+00:00  
3                Chile   False  openflights 2025-01-24 18:52:44.140187+00:00  
4                Chile   False  openflights 2025-01-24 18:52:44.140187+00:00  
...                ...     ...          ...                              ...  
6139      Sierra Leone    True  openflights 2025-01-24 18:52:44.140187+00:00  
6140     United States    True  openflights 2025-01-24 18:52:44.140187+00:00  
6141     United States    True  openflights 2025-01-24 18:52:44.140187+00:00  
6142    United Kingdom    True  openflights 2025-01-24 18:52:44.140187+00:00  
6143  Papua New Guinea    True  openflights 2025-01-24 18:52:44.140187+00:00  

[6144 rows x 10 columns]

##### Look for any unmatched countries (as countries will be a FK on this table)

In [57]:
%%bigquery
select distinct name, country
from air_travel_stg.airlines
where country not in (select name from air_travel_int.Country)
order by country

Query is running:   0%|          |

Downloading:   0%|          |

name                country
0                    Sedalia   Boonville Stage Line
1                      Aires                   S.A.
2    Southern Jersey Airways                   ACOM
3        Active Aero Charter            ACTIVE AERO
4                 Aerocenter             AEROCENTER
..                       ...                    ...
210       Sham Wing Airlines   Syrian Arab Republic
211   Empresa (Aero Uruguay)          UNIFORM OSCAR
212             RAF St Athan         UNited Kingdom
213                    Veles                  VELES
214  Ministry of Agriculture               WATCHDOG

[215 rows x 2 columns]

##### Look to see if we can use `soundex()` to detect some matches

In [58]:
%%bigquery
select a.id, a.name, a.country as airline_tbl_country, soundex(a.country) as airline_tbl_soundex, c.name as country_table_country, soundex(c.name) as country_table_soundex, a.active
from air_travel_stg.airlines a, air_travel_int.Country c
where soundex(a.country) = soundex(c.name)

Query is running:   0%|          |

Downloading:   0%|          |

id                    name airline_tbl_country airline_tbl_soundex  \
0      3577        Nada Air Service                Chad                C300   
1      4316  Sahel Aviation Service                Mali                M400   
2      4316  Sahel Aviation Service                Mali                M400   
3        62                Air Togo                Togo                T200   
4       752              Aerocardal               Chile                C400   
...     ...                     ...                 ...                 ...   
11356  3466           Mesa Airlines       United States                U532   
11357   492           Air Southwest      United Kingdom                U532   
11358   492           Air Southwest      United Kingdom                U532   
11359   492           Air Southwest      United Kingdom                U532   
11360  1308            Airlines PNG    Papua New Guinea                P525   

              country_table_country country_table_soundex  active  
0                              Chad                  C300   False  
1                              Mali                  M400   False  
2                            Malawi                  M400   False  
3                              Togo                  T200   False  
4                             Chile                  C400   False  
...                             ...                   ...     ...  
11356  United States Virgin Islands                  U532    True  
11357                United Kingdom                  U532    True  
11358                 United States                  U532    True  
11359  United States Virgin Islands                  U532    True  
11360              Papua New Guinea                  P525    True  

[11361 rows x 7 columns]

##### Don't use soundex due to false positives (e.g. LAP should be in Columbia, not Lybia)

##### Use the LLM to look for country name matches

In [61]:
import vertexai
from vertexai.generative_models import GenerativeModel, Part

prompt = """Find a match for each country based on the master list of 4 countries below.
For example, if I pass you the country 'Syrian Arab Republic', map it to the country 'Syria'.
If there is no good match, return the original country and null.
Don't match to any countries which are not on the master list.
Format your answer as a list of json objects, with the schema: [{current:string, new:string}].

Below is the master list of countries (to match against):
Switzerland
Sri Lanka
South Africa
Syria
"""

unmatched = "Swaziland, Syrian Arab Republic, S.A., WATCHDOG"

vertexai.init(project=project_id, location=region)
model = GenerativeModel(model_name)
resp = model.generate_content([unmatched, prompt])
resp_text = resp.text.replace("```json", "").replace("```", "").replace("\n", "")
print(resp_text)

[  {    "current": "Swaziland",    "new": null  },  {    "current": "Syrian Arab Republic",    "new": "Syria"  },  {    "current": "S.A.",    "new": "South Africa"  },  {    "current": "WATCHDOG",    "new": null  }]


##### Refine prompt and run on entire list of unmatched countries

In [65]:
import json, pandas_gbq

from google.cloud import bigquery
import vertexai
from vertexai.generative_models import GenerativeModel, Part

prompt = """Find a match for each country based on the list of 256 countries below.
For example, if I pass you the country 'Syrian Arab Republic', map it to 'Syria'.
If there is no good match, default to null
Format your answer as a dictionary, with the schema: {current<string>: new<string>}.
For example, {"Syrian Arab Republic": "Syria", "Swaziland": null}
Below are the list of countries you should match against:
"""

bq_client = bigquery.Client()
prompt_sql = "select name from air_travel_int.Country"
rows = bq_client.query_and_wait(prompt_sql)
prompt_countries = ""

for row in rows:
    prompt_countries += f"{row['name']}, "

prompt = prompt + prompt_countries[:-2]  # lose the last comma
#print("prompt:", prompt)

umatched_countries = """select distinct country from air_travel_stg.airlines
where country not in (select name from air_travel_int.Country)
"""

input_str = ""

rows = bq_client.query_and_wait(umatched_countries)

for row in rows:
    input_str += f"{row['country']}, "
input_str = input_str[:-2] # lose the last comma

vertexai.init(project=project_id, location=region)
model = GenerativeModel(model_name)
resp = model.generate_content([input_str, prompt])
resp_text = resp.text.replace("```json", "").replace("```", "").replace("\n", "")
print("results_raw:", resp_text)
replacements = json.loads(resp_text)
print("replacements:", replacements)

# load dataframe and merge results
airline_table = """
select * except (_data_source, _load_time)
from air_travel_stg.airlines
where country is not null
and country not in (select name from air_travel_int.Country)
order by country
"""

df = bq_client.query_and_wait(airline_table).to_dataframe()
#print("orig df:", df.to_string())

df["country"] = df["country"].map(replacements)
#print("new df:", df.to_string())

table_id = "air_travel_int.tmp_airlines_countries_filtered"
pandas_gbq.to_gbq(df, table_id, project_id=project_id, if_exists="replace")

results_raw: {    "Ivory Coast": "Cote d'Ivoire",    "UNited Kingdom": "United Kingdom",    "Democratic Republic of Congo": "DR Congo",    "Swaziland": "Eswatini",    "Cape Verde": "Cabo Verde",    "Kyrgyzstan": "Kyrgyz Republic",    "Somali Republic": "Somalia",    "Syrian Arab Republic": "Syria",    "Republic of Korea": "South Korea",    "Saint Vincent and the Grenadines": "St. Vincent and the Grenadines",    "Saint Kitts and Nevis": "St. Kitts and Nevis",    "Democratic Republic of the Congo": "DR Congo",    "Netherland": "Netherlands",    "Burma": "Myanmar",    "Lao Peoples Democratic Republic": "Laos",    "Congo (Kinshasa)": "DR Congo",    "Hong Kong SAR of China": "Hong Kong",    "Republic of the Congo": "Congo Republic",    "Russian Federation": "Russia",    "Brunei": "Brunei Darussalam",    "Democratic People's Republic of Korea": "North Korea",    "Saint Lucia": "St. Lucia",    "Faroe Islands": "Faeroe Islands",    "Congo (Brazzaville)": "Congo Republic",    "Canada": "Canada"

100%|██████████| 1/1 [00:00<00:00, 7489.83it/s]


In [66]:
%%bigquery
select * from air_travel_int.tmp_airlines_countries_filtered
where country is not null
order by country

Query is running:   0%|          |

Downloading:   0%|          |

id                    name alias  iata icao     callsign  \
0     4255   Royal Brunei Airlines  None    BI  RBA       BRUNEI   
1     1601      Cabo Verde Express  None  None  CVE        KABEX   
2     2873  Inter Islands Airlines  None    H4  IIN         None   
3    11804              Halcyonair  None    7Z   \N       CREOLE   
4    18762              Lina Congo  None    GC   \N         None   
..     ...                     ...   ...   ...  ...          ...   
144   4586    Syrian Arab Airlines  None    RB  SYR    SYRIANAIR   
145   1975       Damascene Airways  None  None  DAS       AIRDAM   
146   3808              Orient Air  None  None  OVV    ORIENTSYR   
147   4321      Sham Wing Airlines  None  None  SAW     SHAMWING   
148   4121            RAF St Athan  None  None  STN  SAINT ATHAN   

               country  active  
0    Brunei Darussalam    True  
1           Cabo Verde   False  
2           Cabo Verde   False  
3           Cabo Verde    True  
4       Congo Republic   False  
..                 ...     ...  
144              Syria    True  
145              Syria   False  
146              Syria   False  
147              Syria   False  
148     United Kingdom   False  

[149 rows x 8 columns]

##### Create the final table, reordering the fields

In [70]:
%%bigquery
select id, name, alias, icao, iata, callsign, country, active, _data_source, _load_time
from air_travel_stg.airlines
where country in (select name from air_travel_int.Country)
union distinct
select f.id, f.name, f.alias, f.icao, f.iata, f.callsign, f.country, f.active, a._data_source, a._load_time
from air_travel_int.tmp_airlines_countries_filtered f
join air_travel_stg.airlines a on f.id = a.id
where f.country is not null
order by country

Query is running:   0%|          |

Downloading:   0%|          |

id                    name                   alias icao  iata  \
0      3097                 Kam Air                    None  KMF    RQ   
1      3402       Marcopolo Airways                    None  MCP  None   
2       125  Ariana Afghan Airlines                    None  AFG    FG   
3      1397          Balkh Airlines                    None  BHI  None   
4      3878           Pamir Airways                    None  PIR    NR   
...     ...                     ...                     ...  ...   ...   
6072    608            Air Zimbabwe                    None  AZW    UM   
6073   1328             Air Zambezi                    None  TZT  None   
6074  20051     Fly Africa Zimbabwe  Zimbabwe flyafrica.com  FZW  None   
6075   5210     United Air Charters                    None  UAC  None   
6076   1266         Avient Aviation                    None  SMJ    Z3   

           callsign      country  active _data_source  \
0            KAMGAR  Afghanistan    True  openflights   
1         MARCOPOLO  Afghanistan   False  openflights   
2            ARIANA  Afghanistan    True  openflights   
3            SHARIF  Afghanistan   False  openflights   
4             PAMIR  Afghanistan   False  openflights   
...             ...          ...     ...          ...   
6072   AIR ZIMBABWE     Zimbabwe    True  openflights   
6073        ZAMBEZI     Zimbabwe   False  openflights   
6074  Fresh Express     Zimbabwe    True  openflights   
6075        UNITAIR     Zimbabwe    True  openflights   
6076         AVAVIA     Zimbabwe    True  openflights   

                           _load_time  
0    2025-01-24 18:52:44.140187+00:00  
1    2025-01-24 18:52:44.140187+00:00  
2    2025-01-24 18:52:44.140187+00:00  
3    2025-01-24 18:52:44.140187+00:00  
4    2025-01-24 18:52:44.140187+00:00  
...                               ...  
6072 2025-01-24 18:52:44.140187+00:00  
6073 2025-01-24 18:52:44.140187+00:00  
6074 2025-01-24 18:52:44.140187+00:00  
6075 2025-01-24 18:52:44.140187+00:00  
6076 2025-01-24 18:52:44.140187+00:00  

[6077 rows x 10 columns]

In [71]:
%%bigquery
create or replace table air_travel_int.Airline as
    select id, name, alias, icao, iata, callsign, country, active, _data_source, _load_time
    from air_travel_stg.airlines
    where country in (select name from air_travel_int.Country)
    union distinct
    select f.id, f.name, f.alias, f.icao, f.iata, f.callsign, f.country, f.active, a._data_source, a._load_time
    from air_travel_int.tmp_airlines_countries_filtered f
    join air_travel_stg.airlines a on f.id = a.id
    where f.country is not null
    order by country

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check primary key uniqueness

In [72]:
%%bigquery
select id, count(*) as count
from air_travel_int.Airline
group by id
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [id, count]
Index: []

In [73]:
%%bigquery
select count(*) as final_count
from air_travel_int.Airline

Query is running:   0%|          |

Downloading:   0%|          |

final_count
0         6077

##### Clean up

In [74]:
%%bigquery
drop table if exists air_travel_int.tmp_airlines_countries_filtered

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### `Aircraft` table

In [75]:
%%bigquery
select * from air_travel_stg.aircrafts
where icao is null or iata is null
order by name

Query is running:   0%|          |

Downloading:   0%|          |

name  iata  icao _data_source  \
0                        Airbus A330   330  None  openflights   
1          Airbus A330-700 Beluga XL  None  A337  openflights   
2                        Airbus A340   340  None  openflights   
3                        Airbus A350   350  None  openflights   
4                        Airbus A380   380  None  openflights   
5                            BAe 146   146  None  openflights   
6                   Beechcraft Baron  None  BE58  openflights   
7        Beechcraft Baron / 55 Baron  None  BE55  openflights   
8                         Boeing 727   727  None  openflights   
9                         Boeing 737   737  None  openflights   
10                 Boeing 737 MAX 10   7MJ  None  openflights   
11                        Boeing 747   747  None  openflights   
12                        Boeing 757   757  None  openflights   
13                        Boeing 767   767  None  openflights   
14                        Boeing 777   777  None  openflights   
15                        Boeing 787   787  None  openflights   
16                    Bombardier 415  None  CL2T  openflights   
17  Bombardier BD-100 Challenger 300  None  CL30  openflights   
18                       COMAC C-919  None  C919  openflights   
19                        Cessna 152  None  C152  openflights   
20                       Embraer 175   E75  None  openflights   
21                Embraer Legacy 450  None  E545  openflights   
22        Piper PA-28 (above 200 hp)  None  P28B  openflights   
23        Piper PA-28 (up to 180 hp)  None  P28A  openflights   
24              Piper PA-44 Seminole  None  PA44  openflights   
25                    Tupolev Tu-144  None  T144  openflights   

                         _load_time  
0  2025-01-24 18:55:21.985992+00:00  
1  2025-01-24 18:55:21.985992+00:00  
2  2025-01-24 18:55:21.985992+00:00  
3  2025-01-24 18:55:21.985992+00:00  
4  2025-01-24 18:55:21.985992+00:00  
5  2025-01-24 18:55:21.985992+00:00  
6  2025-01-24 18:55:21.985992+00:00  
7  2025-01-24 18:55:21.985992+00:00  
8  2025-01-24 18:55:21.985992+00:00  
9  2025-01-24 18:55:21.985992+00:00  
10 2025-01-24 18:55:21.985992+00:00  
11 2025-01-24 18:55:21.985992+00:00  
12 2025-01-24 18:55:21.985992+00:00  
13 2025-01-24 18:55:21.985992+00:00  
14 2025-01-24 18:55:21.985992+00:00  
15 2025-01-24 18:55:21.985992+00:00  
16 2025-01-24 18:55:21.985992+00:00  
17 2025-01-24 18:55:21.985992+00:00  
18 2025-01-24 18:55:21.985992+00:00  
19 2025-01-24 18:55:21.985992+00:00  
20 2025-01-24 18:55:21.985992+00:00  
21 2025-01-24 18:55:21.985992+00:00  
22 2025-01-24 18:55:21.985992+00:00  
23 2025-01-24 18:55:21.985992+00:00  
24 2025-01-24 18:55:21.985992+00:00  
25 2025-01-24 18:55:21.985992+00:00

##### Look up the missing icao and iata codes with LLM

In [77]:
import json
import pandas, pandas_gbq
from google.cloud import bigquery
import vertexai
from vertexai.generative_models import GenerativeModel, Part

prompt = """For each aircraft, provide the icao and iata codes that best its description.
For example, if I give you the aircraft 'Boeing 737', return the icao code 'B737' and the iata code '73G'.
If you can't find either code, return null.
Format your answer as a list of dictionaries, with the schema: {name<string>, icao<string>, iata<string>}.
For example, {"name": "Boeing 737", "icao": "B737", "iata": "73G"}
"""

bq_client = bigquery.Client()

input_sql = """select name from air_travel_stg.aircrafts
where icao is null or iata is null
"""

input_str = ""

rows = bq_client.query_and_wait(input_sql)

for row in rows:
    input_str += f"{row['name']}, "
input_str = input_str[:-2] # lose the last comma

vertexai.init(project=project_id, location=region)
model = GenerativeModel(model_name)
resp = model.generate_content([input_str, prompt])
resp_text = resp.text.replace("```json", "").replace("```", "").replace("\n", "")
#print("results_raw:", resp_text)

try:
    replacements = json.loads(resp_text)
except Exception as e:
    print(f"Error converting {resp_text} to json:", e)

print("replacements:", replacements)

df = pandas.DataFrame(replacements)
#print("df:", df.to_string())

table_id = "air_travel_int.tmp_aircrafts"
pandas_gbq.to_gbq(df, table_id, project_id=project_id, if_exists="replace")

replacements: [{'name': 'Airbus A340', 'icao': 'A340', 'iata': '340'}, {'name': 'Boeing 777', 'icao': 'B777', 'iata': '777'}, {'name': 'Boeing 727', 'icao': 'B727', 'iata': '727'}, {'name': 'Embraer 175', 'icao': 'E175', 'iata': 'E75'}, {'name': 'Airbus A350', 'icao': 'A350', 'iata': '350'}, {'name': 'Boeing 737', 'icao': 'B737', 'iata': '73G'}, {'name': 'Boeing 737 MAX 10', 'icao': 'B3XM', 'iata': None}, {'name': 'Airbus A330', 'icao': 'A330', 'iata': '330'}, {'name': 'Boeing 747', 'icao': 'B747', 'iata': '747'}, {'name': 'BAe 146', 'icao': 'B463', 'iata': None}, {'name': 'Boeing 757', 'icao': 'B757', 'iata': '757'}, {'name': 'Boeing 787', 'icao': 'B787', 'iata': '787'}, {'name': 'Airbus A380', 'icao': 'A380', 'iata': '380'}, {'name': 'Boeing 767', 'icao': 'B767', 'iata': '767'}, {'name': 'Airbus A330-700 Beluga XL', 'icao': 'BELU', 'iata': None}, {'name': 'Beechcraft Baron / 55 Baron', 'icao': 'BE55', 'iata': None}, {'name': 'Beechcraft Baron', 'icao': 'BE58', 'iata': None}, {'name':

100%|██████████| 1/1 [00:00<00:00, 7584.64it/s]


In [78]:
%%bigquery
select * from air_travel_int.tmp_aircrafts

Query is running:   0%|          |

Downloading:   0%|          |

name  icao  iata
0                  Boeing 737 MAX 10  B3XM  None
1                            BAe 146  B463  None
2          Airbus A330-700 Beluga XL  BELU  None
3        Beechcraft Baron / 55 Baron  BE55  None
4                   Beechcraft Baron  BE58  None
5                         Cessna 152  C152  None
6                        COMAC C-919  COM9  None
7                     Bombardier 415  CL41  None
8   Bombardier BD-100 Challenger 300  CL30  None
9                 Embraer Legacy 450  E550  None
10        Piper PA-28 (up to 180 hp)  PA28  None
11        Piper PA-28 (above 200 hp)  PA28  None
12              Piper PA-44 Seminole  PA44  None
13                    Tupolev Tu-144  TU44  None
14                       Airbus A330  A330   330
15                       Airbus A340  A340   340
16                       Airbus A350  A350   350
17                       Airbus A380  A380   380
18                        Boeing 727  B727   727
19                        Boeing 737  B737   73G
20                        Boeing 747  B747   747
21                        Boeing 757  B757   757
22                        Boeing 767  B767   767
23                        Boeing 777  B777   777
24                        Boeing 787  B787   787
25                       Embraer 175  E175   E75

##### Merge results into new temp table

In [80]:
%%bigquery
create or replace table air_travel_int.tmp_aircrafts_merged as
    select icao, iata, name, _data_source, _load_time
    from air_travel_stg.aircrafts

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [81]:
%%bigquery
update air_travel_int.tmp_aircrafts_merged m
    set icao = (select icao from air_travel_int.tmp_aircrafts t where t.name = m.name)
    where icao is null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [82]:
%%bigquery
update air_travel_int.tmp_aircrafts_merged m
    set iata = (select iata from air_travel_int.tmp_aircrafts t where t.name = m.name)
    where iata is null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [83]:
%%bigquery
select * from air_travel_int.tmp_aircrafts_merged
where icao is null

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [icao, iata, name, _data_source, _load_time]
Index: []

##### Check uniqueness of primary key field (`icao`)

In [86]:
%%bigquery
select icao, count(*) as count
from air_travel_int.tmp_aircrafts_merged
group by icao
having count(*) > 1

Query is running:   0%|          |

Downloading:   0%|          |

icao  count
0  B463      2
1  B737      2
2  E135      2

In [85]:
%%bigquery
select * from air_travel_int.tmp_aircrafts_merged
where icao in ('B737', 'E135')
order by icao

Query is running:   0%|          |

Downloading:   0%|          |

icao iata            name _data_source                       _load_time
0  B737  737      Boeing 737  openflights 2025-01-24 18:55:21.985992+00:00
1  B737  73G  Boeing 737-700  openflights 2025-01-24 18:55:21.985992+00:00
2  E135  ER3   Embraer RJ135  openflights 2025-01-24 18:55:21.985992+00:00
3  E135  ERD   Embraer RJ140  openflights 2025-01-24 18:55:21.985992+00:00

##### Manually remove the two duplicate records

In [88]:
%%bigquery
delete from air_travel_int.tmp_aircrafts_merged
    where icao = 'B737' and iata = '737';
delete from air_travel_int.tmp_aircrafts_merged
    where icao = 'E135' and iata = 'ERD';

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Create the final table with icao being the primary key

In [89]:
%%bigquery
create or replace table air_travel_int.Aircraft as
    select icao, iata, name, _data_source, _load_time
    from air_travel_int.tmp_aircrafts_merged
    where icao is not null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Clean up

In [135]:
%%bigquery
drop table if exists air_travel_int.tmp_aircrafts;
drop table if exists air_travel_int.tmp_aircrafts_merged;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [90]:
%%bigquery
select count(*) as final_count
from air_travel_int.Aircraft

Query is running:   0%|          |

Downloading:   0%|          |

final_count
0          244

#### `Flight_Routes` table (anomaly type 9)

In [91]:
%%bigquery
select * from air_travel_stg.flight_routes
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

airline_code  airline_id source_airport  source_airport_id dest_airport  \
0           2B         410            TGK               <NA>          DME   
1           2G        1654            KCK               <NA>          IKT   
2           4O       17885            PQM               <NA>          MEX   
3           5Z       18946            PBZ               <NA>          JNB   
4           5Z       18946            PBZ               <NA>          CPT   
5           6E        2850            HYD               <NA>          BBI   
6           6E        2850            HYD               <NA>          MAA   
7           6E        2850            HYD               <NA>          COK   
8           6E        2850            HYD               <NA>          BLR   
9           6E        2850            HYD               <NA>          VTZ   

   dest_airport_id  codeshare  stops equipment _data_source  \
0             4029       <NA>      0       CR2  openflights   
1             2937       <NA>      0       AN4  openflights   
2             1824       <NA>      0       SU9  openflights   
3              813       <NA>      0       BEH  openflights   
4              797       <NA>      0       BEH  openflights   
5             3042       <NA>      0       320  openflights   
6             3144       <NA>      0       320  openflights   
7             3136       <NA>      0       320  openflights   
8             3131       <NA>      0       320  openflights   
9             3066       <NA>      0       320  openflights   

                        _load_time  
0 2025-01-24 18:55:26.925088+00:00  
1 2025-01-24 18:55:26.925088+00:00  
2 2025-01-24 18:55:26.925088+00:00  
3 2025-01-24 18:55:26.925088+00:00  
4 2025-01-24 18:55:26.925088+00:00  
5 2025-01-24 18:55:26.925088+00:00  
6 2025-01-24 18:55:26.925088+00:00  
7 2025-01-24 18:55:26.925088+00:00  
8 2025-01-24 18:55:26.925088+00:00  
9 2025-01-24 18:55:26.925088+00:00

##### See if we have any unmatched airlines which are present in the staging table

In [92]:
%%bigquery
select * from air_travel_stg.airlines
where id in
    (select distinct airline_id
    from air_travel_stg.flight_routes
    where airline_id not in (select id from air_travel_int.Airline))
order by id

Query is running:   0%|          |

Downloading:   0%|          |

id                                       name alias iata  icao  \
0    68                                  Air Tindi  None   8T  None   
1   439                            Alaska Airlines  None   AS   ASA   
2   515  Avianca - Aerovias Nacionales de Colombia  None   AV   AVA   
3  2056                                  Dragonair  None   KA   HDA   

                     callsign               country  active _data_source  \
0                        None  Canadian Territories    True  openflights   
1                        Inc.                ALASKA    True  openflights   
2                        S.A.               AVIANCA    True  openflights   
3   Hong Kong Dragon Airlines                DRAGON    True  openflights   

                        _load_time  
0 2025-01-24 18:52:44.140187+00:00  
1 2025-01-24 18:52:44.140187+00:00  
2 2025-01-24 18:52:44.140187+00:00  
3 2025-01-24 18:52:44.140187+00:00

##### Add the missing airline records from staging and update their country names by hand so that we can keep the unmatched flight routes

In [93]:
%%bigquery
select * from air_travel_int.Country
where name in ('Canada', 'United States', 'Colombia', 'Hong Kong')
order by name

Query is running:   0%|          |

Downloading:   0%|          |

name iso_code dafif_codes _data_source  \
0         Canada       CA        [CA]  openflights   
1       Colombia       CO        [CO]  openflights   
2      Hong Kong       HK        [HK]  openflights   
3  United States       US        [US]  openflights   

                        _load_time  
0 2025-01-24 18:55:09.949985+00:00  
1 2025-01-24 18:55:09.949985+00:00  
2 2025-01-24 18:55:09.949985+00:00  
3 2025-01-24 18:55:09.949985+00:00

In [94]:
%%bigquery
insert into air_travel_int.Airline (id, name, alias, icao, iata, callsign, country, active, _data_source, _load_time)
    select id, name, alias, icao, iata, callsign, country, active, _data_source, _load_time
    from air_travel_stg.airlines
    where country in ('Canadian Territories', 'ALASKA', 'AVIANCA', 'DRAGON')

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [95]:
%%bigquery
update air_travel_int.Airline set country = 'Canada'
    where country = 'Canadian Territories';
update air_travel_int.Airline set country = 'United States'
    where country = 'ALASKA';
update air_travel_int.Airline set country = 'Colombia'
    where country = 'AVIANCA';
update air_travel_int.Airline set country = 'Hong Kong'
    where country = 'DRAGON';

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [96]:
%%bigquery
select * from air_travel_int.Airline
where id in (68, 439, 515, 2056)

Query is running:   0%|          |

Downloading:   0%|          |

id                                       name alias  icao iata  \
0    68                                  Air Tindi  None  None   8T   
1   439                            Alaska Airlines  None   ASA   AS   
2   515  Avianca - Aerovias Nacionales de Colombia  None   AVA   AV   
3  2056                                  Dragonair  None   HDA   KA   

                     callsign        country  active _data_source  \
0                        None         Canada    True  openflights   
1                        Inc.  United States    True  openflights   
2                        S.A.       Colombia    True  openflights   
3   Hong Kong Dragon Airlines      Hong Kong    True  openflights   

                        _load_time  
0 2025-01-24 18:52:44.140187+00:00  
1 2025-01-24 18:52:44.140187+00:00  
2 2025-01-24 18:52:44.140187+00:00  
3 2025-01-24 18:52:44.140187+00:00

##### Confirm that we have no more unmatched airlines

In [97]:
%%bigquery
select * from air_travel_stg.flight_routes
where airline_id not in (select id from air_travel_int.Airline)

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [airline_code, airline_id, source_airport, source_airport_id, dest_airport, dest_airport_id, codeshare, stops, equipment, _data_source, _load_time]
Index: []

##### Look up the icao code for both the source and destination airports, replacing airport_id with icao codes (anomaly type 9). Don't exclude any routes which have missing icao codes

In [98]:
%%bigquery
select f.airline_id, a1.icao as source_airport_icao, f.source_airport as source_airport_iata,
    a2.icao as dest_airport_icao, f.dest_airport as dest_airport_iata,
    f.codeshare, f.stops, f.equipment, f._data_source, f._load_time
from air_travel_stg.flight_routes f join air_travel_stg.airports a1
on f.source_airport_id = a1.airport_id
join air_travel_stg.airports a2 on f.dest_airport_id = a2.airport_id

Query is running:   0%|          |

Downloading:   0%|          |

airline_id source_airport_icao source_airport_iata dest_airport_icao  \
0            1308                AYGA                 GKA              AYNZ   
1            1308                AYGA                 GKA              AYMH   
2            1308                AYGA                 GKA              AYMD   
3            1308                AYGA                 GKA              AYPY   
4             328                AYGA                 GKA              AYPY   
...           ...                 ...                 ...               ...   
67235       10741                ZLJC                 JIC              ZLJQ   
67236        1758                ZLJC                 JIC              ZLJQ   
67237        1758                ZLJC                 JIC              ZBNY   
67238         690                ZWAX                 BPL              ZWWW   
67239         324                RJOI                 IWK              RJTT   

      dest_airport_iata  codeshare  stops    equipment _data_source  \
0                   LAE       <NA>      0          DH8  openflights   
1                   HGU       <NA>      0      DH8 DHT  openflights   
2                   MAG       <NA>      0          DH8  openflights   
3                   POM       <NA>      0          DH8  openflights   
4                   POM       <NA>      0  DH4 DH8 DH3  openflights   
...                 ...        ...    ...          ...          ...   
67235               JGN       <NA>      0          737  openflights   
67236               JGN       True      0          737  openflights   
67237               NAY       True      0          737  openflights   
67238               URC       <NA>      0          E90  openflights   
67239               HND       <NA>      0      737 738  openflights   

                            _load_time  
0     2025-01-24 18:55:26.925088+00:00  
1     2025-01-24 18:55:26.925088+00:00  
2     2025-01-24 18:55:26.925088+00:00  
3     2025-01-24 18:55:26.925088+00:00  
4     2025-01-24 18:55:26.925088+00:00  
...                                ...  
67235 2025-01-24 18:55:26.925088+00:00  
67236 2025-01-24 18:55:26.925088+00:00  
67237 2025-01-24 18:55:26.925088+00:00  
67238 2025-01-24 18:55:26.925088+00:00  
67239 2025-01-24 18:55:26.925088+00:00  

[67240 rows x 10 columns]

##### Materialize results as tmp table

In [99]:
%%bigquery
create or replace table air_travel_int.tmp_flight_routes as
    select f.airline_id, a1.icao as source_airport_icao, f.source_airport as source_airport_iata,
        a2.icao as dest_airport_icao, f.dest_airport as dest_airport_iata,
        f.codeshare, f.stops, f.equipment, f._data_source, f._load_time
    from air_travel_stg.flight_routes f join air_travel_stg.airports a1
    on f.source_airport_id = a1.airport_id
    join air_travel_stg.airports a2 on f.dest_airport_id = a2.airport_id

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Look for records which are missing icao codes

In [100]:
%%bigquery
select *
from air_travel_int.tmp_flight_routes
where source_airport_icao is null
or dest_airport_icao is null

Query is running:   0%|          |

Downloading:   0%|          |

airline_id source_airport_icao source_airport_iata dest_airport_icao  \
0          1500                None                 SAX              None   
1         16726                None                 CKD              None   
2         20963                None                 KPB              None   
3         16262                None                 CGA              None   
4         16262                None                 HYL              None   
..          ...                 ...                 ...               ...   
390        2193                None                 JGS              ZUUU   
391         751                None                 NTG              ZYTL   
392        4611                None                 NTG              ZYTL   
393        4611                None                 NTG              ZYTX   
394         751                None                 NTG              ZYTX   

    dest_airport_iata  codeshare  stops equipment _data_source  \
0                 GHE       <NA>      0       BNI  openflights   
1                 RDV       True      0       CNA  openflights   
2                 PPV       <NA>      0       DHP  openflights   
3                 HYL       <NA>      0       DHP  openflights   
4                 KTB       <NA>      0       DHP  openflights   
..                ...        ...    ...       ...          ...   
390               CTU       <NA>      0       319  openflights   
391               DLC       True      0       738  openflights   
392               DLC       <NA>      0       738  openflights   
393               SHE       <NA>      0       738  openflights   
394               SHE       True      0       738  openflights   

                          _load_time  
0   2025-01-24 18:55:26.925088+00:00  
1   2025-01-24 18:55:26.925088+00:00  
2   2025-01-24 18:55:26.925088+00:00  
3   2025-01-24 18:55:26.925088+00:00  
4   2025-01-24 18:55:26.925088+00:00  
..                               ...  
390 2025-01-24 18:55:26.925088+00:00  
391 2025-01-24 18:55:26.925088+00:00  
392 2025-01-24 18:55:26.925088+00:00  
393 2025-01-24 18:55:26.925088+00:00  
394 2025-01-24 18:55:26.925088+00:00  

[395 rows x 10 columns]

##### Look to see if the iata codes match up to unique records in the Airport table, so that we can determine if they can be used to fill in the missing icao codes

In [101]:
%%bigquery
select iata, count(*) as count
from air_travel_int.Airport
where iata in (select source_airport_iata from air_travel_int.tmp_flight_routes
               where source_airport_icao is null)
group by iata
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [iata, count]
Index: []

In [102]:
%%bigquery
select iata, count(*) as count
from air_travel_int.Airport
where iata in (select dest_airport_iata from air_travel_int.tmp_flight_routes
               where dest_airport_icao is null)
group by iata
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [iata, count]
Index: []

##### Given that all the iata codes are unique, we can use the iata to look up the missing icao codes

In [103]:
%%bigquery
select *
from air_travel_int.Airport
where iata in (select source_airport_iata from air_travel_int.tmp_flight_routes
               where source_airport_icao is null)
or iata in (select dest_airport_iata from air_travel_int.tmp_flight_routes
            where dest_airport_icao is null)

Query is running:   0%|          |

Downloading:   0%|          |

icao iata                           name          city       state  \
0   VOTK  TCR              Tuticorin Airport     Tuticorin  Tamil Nadu   
1   CYKT  YKT                 Klemtu Airport        Klemtu          BC   
2   MZSV  INB           Independence Airport   Mango Creek        None   
3   MZPG  PND            Punta Gorda Airport   Punta Gorda        None   
4   MZBF  TZA  Belize City Municipal Airport   Belize City        None   
5   MZPL  PLJ              Placencia Airport     Placencia        None   
6   MZCK  CUK           Caye Caulker Airport  Caye Caulker        None   
7   GMGM  GLN              Goulimime Airport     Goulimime        None   
8   HLUB  QUB                  Ubari Airport         Ubari        None   
9   HLMS  MRA               Misratah Airport      Misratah        None   
10  OMDL  ZDY                  Dalma Airport  Dalma Island        None   
11  ZWWS  WNH                Wenshan Airport       Wenshan          YN   
12  ZSJA  JGS           Jinggangshan Airport          Jian        None   
13  PKTK  TNK                  Tinak Airport         Tinak        None   

                 country                                   latitude  \
0                  India   8.72416700000000000000000000000000000000   
1                 Canada  52.58333300000000000000000000000000000000   
2                 Belize  16.52194400000000000000000000000000000000   
3                 Belize  16.10240000000000000000000000000000000000   
4                 Belize  17.53440000000000000000000000000000000000   
5                 Belize  16.53694400000000000000000000000000000000   
6                 Belize  17.73470000000000000000000000000000000000   
7                Morocco  29.02669910000000000000000000000000000000   
8                  Libya  26.56750000000000000000000000000000000000   
9                  Libya  32.32500000000000000000000000000000000000   
10  United Arab Emirates  24.50338330000000000000000000000000000000   
11                 China  23.37583300000000000000000000000000000000   
12                 China  26.85689926149999700000000000000000000000   
13      Marshall Islands   7.13333300000000000000000000000000000000   

                                      longitude  altitude      timezone_name  \
0     78.02583300000000000000000000000000000000       129      Asia/Calcutta   
1   -128.53333300000000000000000000000000000000         0  America/Vancouver   
2    -88.41058300000000000000000000000000000000        18     America/Belize   
3    -88.80830000000000000000000000000000000000         7     America/Belize   
4    -88.29800000000000000000000000000000000000        15     America/Belize   
5    -88.36166700000000000000000000000000000000        42     America/Belize   
6    -88.03250000000000000000000000000000000000         1     America/Belize   
7    -10.05029960000000000000000000000000000000       984  Africa/Casablanca   
8     12.82310000000000000000000000000000000000      1387     Africa/Tripoli   
9     15.06100000000000000000000000000000000000        60     Africa/Tripoli   
10    52.33605280000000000000000000000000000000         8         Asia/Dubai   
11   104.24305600000000000000000000000000000000      1000      Asia/Shanghai   
12   114.73699951200000000000000000000000000000       281      Asia/Shanghai   
13   171.91666700000000000000000000000000000000         4     Pacific/Majuro   

    timezone_delta daylight_savings_time     type       source _data_source  \
0             <NA>                     N  airport         User  openflights   
1               -8                     A  airport         User  openflights   
2               -6                     N  airport         User  openflights   
3               -6                     U  airport         User  openflights   
4               -6                     N  airport         User  openflights   
5               -6                     U  airport         User  openflights   
6               -6                     U  airport         User  openfligh

In [104]:
%%bigquery
update air_travel_int.tmp_flight_routes
    set source_airport_icao = 'ZSJA' where source_airport_iata = 'JGS'

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Look to see which equipment codes are present in the parent `Aircraft` table

In [105]:
%%bigquery
select distinct equipment
from air_travel_int.tmp_flight_routes
where equipment in (select iata from air_travel_int.Aircraft)

Query is running:   0%|          |

Downloading:   0%|          |

equipment
0         DHP
1         BNI
2         DHT
3         BH2
4         320
..        ...
108       A40
109       A81
110       TU5
111       T20
112       YK4

[113 rows x 1 columns]

##### How many equipment codes are not present?

In [106]:
%%bigquery
select distinct equipment
from air_travel_int.tmp_flight_routes
where equipment not in (select iata from air_travel_int.Aircraft)
order by length(equipment) desc

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [equipment]
Index: []

##### Note: there can be more than one aircraft type per flight route (e.g. 330, 738, 321, 320). We will decompose this relationship into its own table so that we can easily query it with SQL. This resolves anomaly type 8.

In [107]:
%%bigquery
select * from air_travel_int.Aircraft
where iata in ('319', '320', '321', '73G', '752', 'E90', '73H')

Query is running:   0%|          |

Downloading:   0%|          |

icao iata            name _data_source                       _load_time
0  A319  319     Airbus A319  openflights 2025-01-24 18:55:21.985992+00:00
1  A320  320     Airbus A320  openflights 2025-01-24 18:55:21.985992+00:00
2  A321  321     Airbus A321  openflights 2025-01-24 18:55:21.985992+00:00
3  B737  73G  Boeing 737-700  openflights 2025-01-24 18:55:21.985992+00:00
4  B752  752  Boeing 757-200  openflights 2025-01-24 18:55:21.985992+00:00
5  E190  E90     Embraer 190  openflights 2025-01-24 18:55:21.985992+00:00

##### Assign a new PK to the flight routes table, so that we can have a single field to uniquely identify each route. Split off the route id and equipment into a junction table to model the many-to-many.

In [108]:
%%bigquery
select row_number() over () as route_id,
    airline_id, source_airport_icao, dest_airport_icao, codeshare, stops, equipment, _data_source, _load_time
    from air_travel_int.tmp_flight_routes
    where airline_id is not null
    and source_airport_icao is not null
    and dest_airport_icao is not null

Query is running:   0%|          |

Downloading:   0%|          |

route_id  airline_id source_airport_icao dest_airport_icao  codeshare  \
0             1        4797                AGGH              AGAR       <NA>   
1             2        4797                AGGK              AGAR       <NA>   
2             3        4797                AGGH              AGAT       <NA>   
3             4        4797                AGGH              AGGC       <NA>   
4             5        4797                AGGN              AGGC       <NA>   
...         ...         ...                 ...               ...        ...   
66394     66395         751                ZSQD              ZYYJ       True   
66395     66396        4599                ZSQD              ZYYJ       <NA>   
66396     66397        1758                ZSQD              ZYYJ       <NA>   
66397     66398        1767                ZYCC              ZYYJ       <NA>   
66398     66399        1767                ZYTL              ZYYJ       <NA>   

       stops equipment _data_source                       _load_time  
0          0       DHT  openflights 2025-01-24 18:55:26.925088+00:00  
1          0       DHT  openflights 2025-01-24 18:55:26.925088+00:00  
2          0       BNI  openflights 2025-01-24 18:55:26.925088+00:00  
3          0       DHT  openflights 2025-01-24 18:55:26.925088+00:00  
4          0       DHT  openflights 2025-01-24 18:55:26.925088+00:00  
...      ...       ...          ...                              ...  
66394      0       737  openflights 2025-01-24 18:55:26.925088+00:00  
66395      0       737  openflights 2025-01-24 18:55:26.925088+00:00  
66396      0       320  openflights 2025-01-24 18:55:26.925088+00:00  
66397      0   320 321  openflights 2025-01-24 18:55:26.925088+00:00  
66398      0       319  openflights 2025-01-24 18:55:26.925088+00:00  

[66399 rows x 9 columns]

##### Materialize results to temp table, while excluding the records which are missing one of the primary key fields

In [109]:
%%bigquery
create or replace table air_travel_int.tmp_flight_routes_id as
    select row_number() over () as route_id,
    airline_id, source_airport_icao, dest_airport_icao, codeshare, stops, equipment, _data_source, _load_time
    from air_travel_int.tmp_flight_routes
    where airline_id is not null
    and source_airport_icao is not null
    and dest_airport_icao is not null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [110]:
%%bigquery
select * from air_travel_int.tmp_flight_routes_id

Query is running:   0%|          |

Downloading:   0%|          |

route_id  airline_id source_airport_icao dest_airport_icao  codeshare  \
0            12        4797                AGGM              AGGH       <NA>   
1            30        4797                AGGT              AGGK       <NA>   
2            71        1308                AYPY              AYGA       <NA>   
3            92         328                AYTK              AYKV       <NA>   
4           113         328                AYWK              AYMH       <NA>   
...         ...         ...                 ...               ...        ...   
66394     66245        4608                ZYHB              ZYTL       <NA>   
66395     66297        1767                ZGGG              ZYTX       <NA>   
66396     66299         751                ZGGG              ZYTX       True   
66397     66303         751                ZGSZ              ZYTX       True   
66398     66365        1758                ZSSS              ZYTX       True   

       stops equipment _data_source                       _load_time  
0          0   DH8 DHT  openflights 2025-01-24 18:55:26.925088+00:00  
1          0       DHT  openflights 2025-01-24 18:55:26.925088+00:00  
2          0       DH8  openflights 2025-01-24 18:55:26.925088+00:00  
3          0       100  openflights 2025-01-24 18:55:26.925088+00:00  
4          0       100  openflights 2025-01-24 18:55:26.925088+00:00  
...      ...       ...          ...                              ...  
66394      0       320  openflights 2025-01-24 18:55:26.925088+00:00  
66395      0   320 319  openflights 2025-01-24 18:55:26.925088+00:00  
66396      0       320  openflights 2025-01-24 18:55:26.925088+00:00  
66397      0       320  openflights 2025-01-24 18:55:26.925088+00:00  
66398      0       738  openflights 2025-01-24 18:55:26.925088+00:00  

[66399 rows x 9 columns]

##### Yes, technically we shifted the primary key to `route_id`, but the natural key is still {`airline_id`, `source_airport_icao`, `dest_airport_icao`}, so we should ensure uniqueness of those fields

In [111]:
%%bigquery
select airline_id, source_airport_icao, dest_airport_icao, count(*) as count
from air_travel_int.tmp_flight_routes_id
group by airline_id, source_airport_icao, dest_airport_icao
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [airline_id, source_airport_icao, dest_airport_icao, count]
Index: []

##### Create a new junction table, `Route_Equipment`, to model the many-to-many between `Flight_Routes` and `Aircraft` (i.e. a route can have multiple equipment types and an equipment type can be used by multiple routes). We will create the final table for `Flight_Routes` after creating the junction table.

In [112]:
%%bigquery
select route_id, split(equipment, ' ') as equipment_array from air_travel_int.tmp_flight_routes_id

Query is running:   0%|          |

Downloading:   0%|          |

route_id equipment_array
0            12      [DH8, DHT]
1            30           [DHT]
2            71           [DH8]
3            92           [100]
4           113           [100]
...         ...             ...
66394     66245           [320]
66395     66297      [320, 319]
66396     66299           [320]
66397     66303           [320]
66398     66365           [738]

[66399 rows x 2 columns]

##### Materialize to temp table

In [113]:
%%bigquery
create or replace table air_travel_int.tmp_route_equipment as
    select route_id, split(equipment, ' ') as equipment_array
    from air_travel_int.tmp_flight_routes_id
    where equipment is not null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [114]:
%%bigquery
select * from air_travel_int.tmp_route_equipment

Query is running:   0%|          |

Downloading:   0%|          |

route_id equipment_array
0          5159           [738]
1          8745           [737]
2         10639           [738]
3         11877           [73G]
4         14266           [767]
...         ...             ...
66378     49320           [CRJ]
66379     51765           [CR2]
66380     60950           [320]
66381     61731           [737]
66382     63423           [738]

[66383 rows x 2 columns]

In [115]:
%%bigquery
select route_id, equipment
from air_travel_int.tmp_route_equipment cross join unnest(equipment_array) as equipment
where equipment != ''

Query is running:   0%|          |

Downloading:   0%|          |

route_id equipment
0          5159       738
1          8745       737
2         10639       738
3         11877       73G
4         14266       767
...         ...       ...
91821     49320       CRJ
91822     51765       CR2
91823     60950       320
91824     61731       737
91825     63423       738

[91826 rows x 2 columns]

##### Materialize unnested results to temp table

In [116]:
%%bigquery
create or replace table air_travel_int.tmp_route_equipment_unnested as
    select route_id, equipment
    from air_travel_int.tmp_route_equipment cross join unnest(equipment_array) as equipment
    where equipment != ''

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Join with the parent table, `Aircraft`, and replace the current iata code with the icao code (anomaly type 9)

In [117]:
%%bigquery
select re.*, a.*
from air_travel_int.tmp_route_equipment_unnested re join air_travel_int.Aircraft a
on a.iata = re.equipment

Query is running:   0%|          |

Downloading:   0%|          |

route_id equipment  icao iata  \
0           228       DH7  DHC7  DH7   
1         30641       736  B736  736   
2         44125       DH2  DH8B  DH2   
3         48020       318  A318  318   
4         39870       340  A340  340   
...         ...       ...   ...  ...   
74693     42586       SF3  SF34  SF3   
74694     18814       SF3  SF34  SF3   
74695     46064       SF3  SF34  SF3   
74696      7870       SF3  SF34  SF3   
74697     15885       SF3  SF34  SF3   

                                            name _data_source  \
0               De Havilland Canada DHC-7 Dash 7  openflights   
1                                 Boeing 737-600  openflights   
2      De Havilland Canada DHC-8-200 Dash 8 / 8Q  openflights   
3                                    Airbus A318  openflights   
4                                    Airbus A340  openflights   
...                                          ...          ...   
74693                              Saab SF340A/B  openflights   
74694                              Saab SF340A/B  openflights   
74695                              Saab SF340A/B  openflights   
74696                              Saab SF340A/B  openflights   
74697                              Saab SF340A/B  openflights   

                            _load_time  
0     2025-01-24 18:55:21.985992+00:00  
1     2025-01-24 18:55:21.985992+00:00  
2     2025-01-24 18:55:21.985992+00:00  
3     2025-01-24 18:55:21.985992+00:00  
4     2025-01-24 18:55:21.985992+00:00  
...                                ...  
74693 2025-01-24 18:55:21.985992+00:00  
74694 2025-01-24 18:55:21.985992+00:00  
74695 2025-01-24 18:55:21.985992+00:00  
74696 2025-01-24 18:55:21.985992+00:00  
74697 2025-01-24 18:55:21.985992+00:00  

[74698 rows x 7 columns]

##### Create the final tables (`Route_Equipment` and `Flight_Routes`)

In [118]:
%%bigquery
create or replace table air_travel_int.Route_Equipment as
    select re.route_id, a.icao as aircraft_icao, a._data_source, a._load_time
    from air_travel_int.tmp_route_equipment_unnested re join air_travel_int.Aircraft a
    on re.equipment = a.iata

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [119]:
%%bigquery
create or replace table air_travel_int.Flight_Routes as
    select route_id, airline_id, source_airport_icao, dest_airport_icao, codeshare, stops, _data_source, _load_time
    from air_travel_int.tmp_flight_routes_id

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [120]:
%%bigquery
select count(*) as final_count
from air_travel_int.Route_Equipment

Query is running:   0%|          |

Downloading:   0%|          |

final_count
0        74698

In [121]:
%%bigquery
select count(*) as final_count
from air_travel_int.Flight_Routes

Query is running:   0%|          |

Downloading:   0%|          |

final_count
0        66399

##### Clean up

In [122]:
%%bigquery
drop table if exists air_travel_int.tmp_route_equipment;
drop table if exists air_travel_int.tmp_route_equipment_unnested;
drop table if exists air_travel_int.tmp_flight_routes;
drop table if exists air_travel_int.tmp_flight_routes_id;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### `Flight_Delays`

In [123]:
%%bigquery
select * from air_travel_stg.flight_delays
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

event_month carrier            carrier_name airport_code airport_city  \
0  2003-09-01      TZ  ATA Airlines d/b/a ATA          ABQ  Albuquerque   
1  2004-03-01      TZ  ATA Airlines d/b/a ATA          BWI    Baltimore   
2  2006-01-01      TZ  ATA Airlines d/b/a ATA          BWI    Baltimore   
3  2004-06-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   
4  2005-01-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   
5  2004-07-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   
6  2004-08-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   
7  2004-03-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   
8  2003-08-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   
9  2004-01-01      TZ  ATA Airlines d/b/a ATA          CLT    Charlotte   

  airport_state                                       airport_name  arr_total  \
0            NM                  Albuquerque International Sunport       <NA>   
1            MD   Baltimore/Washington International Thurgood M...       <NA>   
2            MD   Baltimore/Washington International Thurgood M...       <NA>   
3            NC                    Charlotte Douglas International        108   
4            NC                    Charlotte Douglas International          8   
5            NC                    Charlotte Douglas International        106   
6            NC                    Charlotte Douglas International        111   
7            NC                    Charlotte Douglas International        112   
8            NC                    Charlotte Douglas International        110   
9            NC                    Charlotte Douglas International        107   

   arr_cancelled  arr_diverted  arr_delay_min  weather_delay_min  \
0           <NA>          <NA>           <NA>               <NA>   
1           <NA>          <NA>           <NA>               <NA>   
2           <NA>          <NA>           <NA>               <NA>   
3              1             0           1704                  0   
4              0             0             86                  0   
5              0             0           1687                  0   
6              0             0            842                  0   
7              0             0            479                  0   
8              0             0           1187                  0   
9              5             0           1798                176   

   nas_delay_min  late_aircraft_delay_min _data_source  \
0           <NA>                     <NA>    transtats   
1           <NA>                     <NA>    transtats   
2           <NA>                     <NA>    transtats   
3            767                      812    transtats   
4             24                        5    transtats   
5            504                      932    transtats   
6            323                      252    transtats   
7             78                      287    transtats   
8            482                      392    transtats   
9            334                      978    transtats   

                        _load_time  
0 2025-01-24 18:52:28.819379+00:00  
1 2025-01-24 18:52:28.819379+00:00  
2 2025-01-24 18:52:28.819379+00:00  
3 2025-01-24 18:52:28.819379+00:00  
4 2025-01-24 18:52:28.819379+00:00  
5 2025-01-24 18:52:28.819379+00:00  
6 2025-01-24 18:52:28.819379+00:00  
7 2025-01-24 18:52:28.819379+00:00  
8 2025-01-24 18:52:28.819379+00:00  
9 2025-01-24 18:52:28.819379+00:00

In [124]:
%%bigquery
select event_month, carrier, airport_code, count(*) as count
from air_travel_stg.flight_delays
group by event_month, carrier, airport_code
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [event_month, carrier, airport_code, count]
Index: []

##### Standardize the airport and airline identifiers

##### Note: all carriers are present in the airline table

In [125]:
%%bigquery
select distinct airport_code, airport_city, airport_state, airport_name, _data_source, _load_time
from air_travel_stg.flight_delays
where airport_code not in (select iata from air_travel_int.Airport
                           where country = 'United States')

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [airport_code, airport_city, airport_state, airport_name, _data_source, _load_time]
Index: []

##### Note: all airports can be joined successfully

In [126]:
%%bigquery
select distinct fd.event_month, fd.carrier, fd.carrier_name, ap.icao as airport_icao,
    fd.arr_total, fd.arr_cancelled, fd.arr_diverted, fd.arr_delay_min,
    fd.weather_delay_min, fd.nas_delay_min, fd.late_aircraft_delay_min,
    fd._data_source, fd._load_time
from air_travel_stg.flight_delays fd join air_travel_int.Airport ap
on fd.airport_code = ap.iata
where ap.country = 'United States'

Query is running:   0%|          |

Downloading:   0%|          |

event_month carrier            carrier_name airport_icao  arr_total  \
0       2003-09-01      TZ  ATA Airlines d/b/a ATA         KABQ       <NA>   
1       2004-03-01      TZ  ATA Airlines d/b/a ATA         KBWI       <NA>   
2       2006-01-01      TZ  ATA Airlines d/b/a ATA         KBWI       <NA>   
3       2004-06-01      TZ  ATA Airlines d/b/a ATA         KCLT        108   
4       2005-01-01      TZ  ATA Airlines d/b/a ATA         KCLT          8   
...            ...     ...                     ...          ...        ...   
376100  2017-11-01      VX          Virgin America         KIAD        115   
376101  2014-06-01      VX          Virgin America         KIAD        151   
376102  2013-09-01      VX          Virgin America         KIAD        117   
376103  2012-01-01      VX          Virgin America         KIAD        159   
376104  2013-11-01      VX          Virgin America         KIAD        127   

        arr_cancelled  arr_diverted  arr_delay_min  weather_delay_min  \
0                <NA>          <NA>           <NA>               <NA>   
1                <NA>          <NA>           <NA>               <NA>   
2                <NA>          <NA>           <NA>               <NA>   
3                   1             0           1704                  0   
4                   0             0             86                  0   
...               ...           ...            ...                ...   
376100              2             0            852                  4   
376101              0             0            971                 38   
376102              0             0            878                 58   
376103              1             1           1010                 92   
376104              0             0            684                136   

        nas_delay_min  late_aircraft_delay_min _data_source  \
0                <NA>                     <NA>    transtats   
1                <NA>                     <NA>    transtats   
2                <NA>                     <NA>    transtats   
3                 767                      812    transtats   
4                  24                        5    transtats   
...               ...                      ...          ...   
376100            158                      300    transtats   
376101            576                      223    transtats   
376102            217                      402    transtats   
376103              0                      475    transtats   
376104              1                      247    transtats   

                             _load_time  
0      2025-01-24 18:52:28.819379+00:00  
1      2025-01-24 18:52:28.819379+00:00  
2      2025-01-24 18:52:28.819379+00:00  
3      2025-01-24 18:52:28.819379+00:00  
4      2025-01-24 18:52:28.819379+00:00  
...                                 ...  
376100 2025-01-24 18:52:28.819379+00:00  
376101 2025-01-24 18:52:28.819379+00:00  
376102 2025-01-24 18:52:28.819379+00:00  
376103 2025-01-24 18:52:28.819379+00:00  
376104 2025-01-24 18:52:28.819379+00:00  

[376105 rows x 13 columns]

##### Materialize results to temp table

In [127]:
%%bigquery
create or replace table air_travel_int.tmp_flight_delays as
    select distinct fd.event_month, fd.carrier, fd.carrier_name, ap.icao as airport_icao,
        fd.arr_total, fd.arr_cancelled, fd.arr_diverted, fd.arr_delay_min,
        fd.weather_delay_min, fd.nas_delay_min, fd.late_aircraft_delay_min,
        fd._data_source, fd._load_time
    from air_travel_stg.flight_delays fd join air_travel_int.Airport ap
    on fd.airport_code = ap.iata
    where ap.country = 'United States'

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [128]:
%%bigquery
select * from air_travel_int.tmp_flight_delays

Query is running:   0%|          |

Downloading:   0%|          |

event_month carrier            carrier_name airport_icao  arr_total  \
0       2006-01-01      TZ  ATA Airlines d/b/a ATA         KBWI       <NA>   
1       2004-08-01      TZ  ATA Airlines d/b/a ATA         KCLT        111   
2       2004-05-01      TZ  ATA Airlines d/b/a ATA         KDFW        135   
3       2004-07-01      TZ  ATA Airlines d/b/a ATA         PHNL        131   
4       2005-09-01      TZ  ATA Airlines d/b/a ATA         KDEN        174   
...            ...     ...                     ...          ...        ...   
376100  2015-12-01      VX          Virgin America         KDCA        117   
376101  2017-05-01      VX          Virgin America         KSLC          1   
376102  2017-02-01      VX          Virgin America         KSFO       1511   
376103  2018-03-01      VX          Virgin America         KSEA        443   
376104  2018-02-01      VX          Virgin America         KIAD        104   

        arr_cancelled  arr_diverted  arr_delay_min  weather_delay_min  \
0                <NA>          <NA>           <NA>               <NA>   
1                   0             0            842                  0   
2                   0             0           2067                 33   
3                   0             0           1235                  0   
4                   0             0           1029                  0   
...               ...           ...            ...                ...   
376100              1             0           1221                281   
376101              0             1              0                  0   
376102             68            27          42792               3252   
376103             13             0           6701                  0   
376104              1             0             71                  0   

        nas_delay_min  late_aircraft_delay_min _data_source  \
0                <NA>                     <NA>    transtats   
1                 323                      252    transtats   
2                 992                      772    transtats   
3                 203                      482    transtats   
4                 168                      431    transtats   
...               ...                      ...          ...   
376100            192                      188    transtats   
376101              0                        0    transtats   
376102          29951                     6209    transtats   
376103           1608                     2378    transtats   
376104             18                        0    transtats   

                             _load_time  
0      2025-01-24 18:52:28.819379+00:00  
1      2025-01-24 18:52:28.819379+00:00  
2      2025-01-24 18:52:28.819379+00:00  
3      2025-01-24 18:52:28.819379+00:00  
4      2025-01-24 18:52:28.819379+00:00  
...                                 ...  
376100 2025-01-24 18:52:28.819379+00:00  
376101 2025-01-24 18:52:28.819379+00:00  
376102 2025-01-24 18:52:28.819379+00:00  
376103 2025-01-24 18:52:28.819379+00:00  
376104 2025-01-24 18:52:28.819379+00:00  

[376105 rows x 13 columns]

In [129]:
%%bigquery
select distinct carrier, carrier_name
from air_travel_int.tmp_flight_delays
where carrier not in (select iata from air_travel_int.Airline
                      where country = 'United States')

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [carrier, carrier_name]
Index: []

In [130]:
%%bigquery
select fd.event_month, al.id as airline_id, fd.airport_icao, fd.arr_total, fd.arr_cancelled,
    fd.arr_diverted, fd.arr_delay_min, fd.weather_delay_min, fd.nas_delay_min, fd.late_aircraft_delay_min,
    fd._data_source, fd._load_time
from air_travel_int.tmp_flight_delays fd join air_travel_int.Airline al
on fd.carrier = al.iata
where al.country = 'United States'

Query is running:   0%|          |

Downloading:   0%|          |

event_month  airline_id airport_icao  arr_total  arr_cancelled  \
0       2022-11-01         282         KSPI         32              0   
1       2023-08-01         282         KBHM          2              0   
2       2019-06-01         282         KFNT         23              0   
3       2019-12-01         282         KBIS          4              0   
4       2020-02-01         282         KBIS         54              1   
...            ...         ...          ...        ...            ...   
381152  2015-12-01        5331         KDCA        117              1   
381153  2017-05-01        5331         KSLC          1              0   
381154  2017-02-01        5331         KSFO       1511             68   
381155  2018-03-01        5331         KSEA        443             13   
381156  2018-02-01        5331         KIAD        104              1   

        arr_diverted  arr_delay_min  weather_delay_min  nas_delay_min  \
0                  0           1158                  0             40   
1                  0              0                  0              0   
2                  0            598                 65             27   
3                  0             46                  0             37   
4                  0           1343                  0            147   
...              ...            ...                ...            ...   
381152             0           1221                281            192   
381153             1              0                  0              0   
381154            27          42792               3252          29951   
381155             0           6701                  0           1608   
381156             0             71                  0             18   

        late_aircraft_delay_min _data_source                       _load_time  
0                           321    transtats 2025-01-24 18:52:28.819379+00:00  
1                             0    transtats 2025-01-24 18:52:28.819379+00:00  
2                           241    transtats 2025-01-24 18:52:28.819379+00:00  
3                             0    transtats 2025-01-24 18:52:28.819379+00:00  
4                           895    transtats 2025-01-24 18:52:28.819379+00:00  
...                         ...          ...                              ...  
381152                      188    transtats 2025-01-24 18:52:28.819379+00:00  
381153                        0    transtats 2025-01-24 18:52:28.819379+00:00  
381154                     6209    transtats 2025-01-24 18:52:28.819379+00:00  
381155                     2378    transtats 2025-01-24 18:52:28.819379+00:00  
381156                        0    transtats 2025-01-24 18:52:28.819379+00:00  

[381157 rows x 12 columns]

##### Create final table

In [131]:
%%bigquery
create or replace table air_travel_int.Flight_Delays as
    select fd.event_month, al.id as airline_id, fd.airport_icao, fd.arr_total, fd.arr_cancelled,
        fd.arr_diverted, fd.arr_delay_min, fd.weather_delay_min, fd.nas_delay_min, fd.late_aircraft_delay_min,
        fd._data_source, fd._load_time
    from air_travel_int.tmp_flight_delays fd join air_travel_int.Airline al
    on fd.carrier = al.iata
    where al.country = 'United States'

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check uniqueness of primary key fields (`event_month`, `airline_id`, `airport_icao`)

In [132]:
%%bigquery
select event_month, airline_id, airport_icao, count(*) as count
from air_travel_int.Flight_Delays
group by event_month, airline_id, airport_icao
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [event_month, airline_id, airport_icao, count]
Index: []

In [133]:
%%bigquery
select count(*) as final_count
from air_travel_int.Flight_Delays

Query is running:   0%|          |

Downloading:   0%|          |

final_count
0       381157

##### Clean up

In [134]:
%%bigquery
drop table if exists air_travel_int.tmp_flight_delays

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### Key Constraints
##### More details on how primary and foreign keys work in BQ: [link](https://cloud.google.com/blog/products/data-analytics/join-optimizations-with-bigquery-primary-and-foreign-keys?e=48754805)

##### Primary keys

In [136]:
%%bigquery
alter table air_travel_int.Aircraft add primary key (icao) not enforced;
alter table air_travel_int.Airline add primary key (id) not enforced;
alter table air_travel_int.Airport add primary key (icao) not enforced;
alter table air_travel_int.Airport_Businesses add primary key (icao, terminal, business, location) not enforced;
alter table air_travel_int.Airport_Review add primary key (id) not enforced;
alter table air_travel_int.Business add primary key (name) not enforced;
alter table air_travel_int.Country add primary key (name) not enforced;
alter table air_travel_int.Flight_Delays add primary key (event_month, airline_id, airport_icao) not enforced;
alter table air_travel_int.Flight_Routes add primary key (route_id) not enforced;
alter table air_travel_int.Menu_Items add primary key (business_name, menu_item) not enforced;
alter table air_travel_int.Route_Equipment add primary key (route_id, aircraft_icao) not enforced;
alter table air_travel_int.TSA_Traffic add primary key (event_date, event_hour, airport_icao, tsa_checkpoint) not enforced;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Foreign keys

In [137]:
%%bigquery
alter table air_travel_int.Airline add constraint airline_fk_country foreign key (country)
    references air_travel_int.Country (name) not enforced;
alter table air_travel_int.Airport add constraint airport_fk_country foreign key (country)
    references air_travel_int.Country (name) not enforced;
alter table air_travel_int.Airport_Businesses add constraint airport_business_fk_icao foreign key (icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Airport_Review add constraint airport_reviews_fk_icao foreign key (icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Flight_Delays add constraint flight_delays_fk_airline_id foreign key (airline_id)
    references air_travel_int.Airline (id) not enforced;
alter table air_travel_int.Flight_Delays add constraint flight_delays_fk_airport_icao foreign key (airport_icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Flight_Routes add constraint flight_routes_fk_airline_id foreign key (airline_id)
    references air_travel_int.Airline (id) not enforced;
alter table air_travel_int.Flight_Routes add constraint flight_routes_fk_source_airport_icao foreign key (source_airport_icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Flight_Routes add constraint flight_routes_fk_dest_airport_icao foreign key (dest_airport_icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Menu_Items add constraint menu_items_fk_business_name foreign key (business_name)
    references air_travel_int.Business (name) not enforced;
alter table air_travel_int.Route_Equipment add constraint route_equipment_fk_route_id foreign key (route_id)
    references air_travel_int.Flight_Routes (route_id) not enforced;
alter table air_travel_int.Route_Equipment add constraint route_equipment_fk_aircraft_icao foreign key (aircraft_icao)
    references air_travel_int.Aircraft (icao) not enforced;
alter table air_travel_int.TSA_Traffic add constraint tsa_traffic_fk_airport_icao foreign key (airport_icao)
    references air_travel_int.Airport (icao) not enforced;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### Restart the runtime
##### Run this cell only if you see that code changes aren't getting picked up. Be sure to save your work before running.

In [ ]:
import os
os.kill(os.getpid(), 9)